In [1]:
from collections import namedtuple
import numpy as np
import pandas as pd
from pathlib import Path

# Display more rows and get rid of the margins
pd.set_option('display.max_rows', 500)
pd.set_option('display.max_columns', 500)
pd.set_option('max_colwidth',500)
from IPython.core.display import display, HTML
display(HTML("<style>.container { width:100% !important; }</style>"))

# Display mulitiple values from each cell
# https://stackoverflow.com/a/42476224
from IPython.core.interactiveshell import InteractiveShell
InteractiveShell.ast_node_interactivity = "all"

# Define paths and functions

In [5]:
abcd_table_path = './ABCDstudyDEAP/'
data_dir = Path('data')

In [6]:
def load_abcd_table(path):
    table = pd.read_csv(path, skiprows=[1], header=0, sep='\t')
    labels = pd.read_csv(path, nrows=1, header=0, sep='\t')
    labels = labels.T.reset_index().rename(columns={'index':'name', 0:'doc'})
    return table, labels

def append_abcd_table(path, table=None, label=None, on=None):
    if table is None:
        return load_abcd_table(path)
    if on is None:
        on = ['subjectkey', 'interview_date', 'visit', 'lmt_run']
    new_table, new_label = load_abcd_table(path)
    # Find drop common columns that aren't in the set we're merging on
    drop_cols = label.loc[label.doc.isin(new_label.doc) & ~label.name.isin(on),'name'].values
    new_table.drop(drop_cols, axis=1, inplace=True)
    new_label = new_label[~new_label.name.isin(drop_cols) & ~new_label.name.isin(on)]
    
    # Get table shapes for error checking
    ts = table.shape
    nts = new_table.shape
    ls = label.shape
    nls = new_label.shape
    
    # Merge the tables
    table = table.merge(new_table, how='outer',on=on)
    
    # Check for success
    assert table.shape[0] == ts[0] == nts[0]
    assert table.shape[1] == (ts[1] + nts[1] - len(on))
    
    # Merge labels
    label = pd.concat([label, new_label]).reset_index(drop=True)
    
    assert label.shape[0] == table.shape[1]
    
    return table, label

def load_task_melt_contrasts(paths, contrasts, task_name):
    task_t = None
    task_l = None
    for pp in paths:
        task_t, task_l = append_abcd_table(pp, table=task_t, label=task_l)
        
    # Rearrange columns
    new_col_order = pd.concat([task_l.name[~task_l.doc.str.split('for ').str[1].str.split(' contrast in').str[0].isin(contrasts)],
                               task_l.name[task_l.doc.str.split('for ').str[1].str.split(' contrast in').str[0].isin(contrasts)]]).values
    task_t = task_t.loc[:,new_col_order]
    task_l = task_l.set_index('name').T.loc[:,new_col_order].T.reset_index()
    
    # Manipulate labels to get more information about them
    if task_name == 'nb':
        task_l.loc[task_l.doc.str.split('for ').str[1].str.split(' in').str[0].isin(contrasts), 'contrast'] = task_l.doc.str.split('for ').str[1].str.split(' in').str[0]
        task_l.loc[pd.notnull(task_l.contrast),'roi_code'] = task_l.loc[pd.notnull(task_l.contrast),'name'].str.split('x').str[-1]
        task_l.loc[pd.notnull(task_l.contrast),'hemisphere'] = task_l.loc[pd.notnull(task_l.contrast),'roi_code'].str.split('g').str[0]
        task_l.loc[pd.notnull(task_l.contrast),'roi_num'] = task_l.loc[pd.notnull(task_l.contrast),'roi_code'].str.split('p').str[-1].astype(int)
        task_meta_cols = task_l.name[~task_l.doc.str.split('for ').str[1].str.split(' in').str[0].isin(contrasts)]
    else:
        task_l.loc[task_l.doc.str.split('for ').str[1].str.split(' contrast in').str[0].isin(contrasts), 'contrast'] = task_l.doc.str.split('for ').str[1].str.split(' contrast in').str[0]
        task_l.loc[pd.notnull(task_l.contrast),'roi_code'] = task_l.loc[pd.notnull(task_l.contrast),'name'].str.split('x').str[-1]
        task_l.loc[pd.notnull(task_l.contrast),'hemisphere'] = task_l.loc[pd.notnull(task_l.contrast),'roi_code'].str.split('g').str[0]
        task_l.loc[pd.notnull(task_l.contrast),'roi_num'] = task_l.loc[pd.notnull(task_l.contrast),'roi_code'].str.split('p').str[-1].astype(int)
        task_meta_cols = task_l.name[~task_l.doc.str.split('for ').str[1].str.split(' contrast in').str[0].isin(contrasts)]

    task_t_melt = []
    for contrast in contrasts:
        tmpdf = task_t.loc[:,task_meta_cols]
        tmpdf['contrast'] = contrast
        if task_name == 'nb':
            contrast_cols = task_l.name[task_l.doc.str.split('for ').str[1].str.split(' in').str[0] == contrast].values
        else:
            contrast_cols = task_l.name[task_l.doc.str.split('for ').str[1].str.split(' contrast in').str[0] == contrast].values
        contrast_df = task_t.loc[:,contrast_cols]
        contrast_df.columns = [task_l.loc[task_l.name==cc,'roi_code'].values[0] for cc in contrast_df.columns.values]
        task_t_melt.append(pd.concat([tmpdf,contrast_df], axis=1))
    task_t_melt = pd.concat(task_t_melt)
    task_t_melt['task'] = task_name
    return task_t_melt, task_l

# Prepare data
## Get sex, handedness, age and device data for balancing

In [7]:
# Get Handedness data
ehis_path = abcd_table_path + 'abcd_ehis01.txt'
ehis = pd.read_csv(ehis_path, skiprows=[1], header=0, sep='\t')
ehis_labels = pd.read_csv(ehis_path, nrows = 1, header = 0, sep='\t')
ehis_labels = ehis_labels.T.reset_index().rename(columns={'index':'name', 0:'doc'})

In [9]:
ehis_labels

name  \
0         collection_id   
1        abcd_ehis01_id   
2            dataset_id   
3            subjectkey   
4        src_subject_id   
5        interview_date   
6         interview_age   
7                gender   
8             eventname   
9                ehi_1b   
10               ehi_2b   
11               ehi_3b   
12               ehi_4b   
13             ehi_time   
14         ehi_ss_score   
15     collection_title   
16  promoted_subjectkey   
17    study_cohort_name   

                                                                                                doc  
0                                                                                     collection_id  
1                                                                                    abcd_ehis01_id  
2                                                                                        dataset_id  
3                                     The NDAR Global Unique Identifier (GUID) for research subject  
4                                                        Subject ID how it's defined in lab/project  
5   Date on which the interview/genetic test/sampling/imaging/biospecimen was completed. MM/DD/YYYY  
6                                 Age in months at the time of the interview/test/sampling/imaging.  
7                                                                                Sex of the subject  
8                                                   The event name for which the data was collected  
9                                                                                           Writing  
10                                                                                         Throwing  
11                                                                                       Toothbrush  
12                                                                                            Spoon  
13                                                                                    Current Time:  
14                                                                          Handedness score rating  
15                                                                                 collection_title  
16                                                                              promoted_subjectkey  
17                                                                                study_cohort_name

In [12]:
# Get site data
site_df = pd.read_csv(abcd_table_path + 'abcd_lt01.txt',
                      skiprows = [1],
                      header = 0,
                      sep='\t')

# Get device data
device_df = pd.read_csv(abcd_table_path + 'abcd_mri01.txt',
                        skiprows = [1],
                        header = 0,
                        sep='\t')

# Put the handedness, age, and sex information together with the device data

bal_site_fields = ['abcd_lt01_id',
                   'subjectkey',
                   'eventname',
                   'site_id_l'
                   ]
bal_ehis_fields = ['collection_id',
                   'dataset_id', 
                   'subjectkey',
                   'interview_age', 
                   'gender',
                   'ehi_ss_score',
                   'eventname'
                  ]
bal_device_fields = ['subjectkey',
                     'eventname',
                     'mri_info_visitid',
                     'mri_info_manufacturer',
                     'mri_info_manufacturersmn',
                     'mri_info_deviceserialnumber',
                     'mri_info_magneticfieldstrength',
                     'mri_info_softwareversion'
                    ]

for_balancing = (ehis.loc[:, bal_ehis_fields]
                     .merge(site_df.loc[:,bal_site_fields],
                            how='outer',
                            on=['subjectkey', 'eventname'],
                            indicator='site_indicator')
                     .merge(device_df.loc[:,bal_device_fields],
                            how='outer',
                            on=['subjectkey', 'eventname'],
                            indicator='device_indicator'))

# make sure both merges worked
assert for_balancing.groupby(['site_indicator'])[['subjectkey']].count().loc['both', 'subjectkey'] == len(ehis)
assert for_balancing.groupby(['device_indicator'])[['subjectkey']].count().loc['both', 'subjectkey'] == len(ehis)

for_balancing = for_balancing.drop(['site_indicator', 'device_indicator'], axis=1)

In [14]:
for_balancing.head()

collection_id  dataset_id        subjectkey  interview_age gender  \
0           2573       16633  NDAR_INV0AU5R8NA            117      F   
1           2573       16633  NDAR_INV0CP9XGTP            128      F   
2           2573       16633  NDAR_INV0CZBUV4C            111      M   
3           2573       16633  NDAR_INV0EWGP0U5            108      M   
4           2573       16633  NDAR_INV0F82C6R8            131      M   

   ehi_ss_score              eventname  abcd_lt01_id site_id_l  \
0             1  baseline_year_1_arm_1             6    site19   
1             1  baseline_year_1_arm_1            18    site05   
2             1  baseline_year_1_arm_1            19    site16   
3             2  baseline_year_1_arm_1            30    site17   
4             1  baseline_year_1_arm_1            32    site17   

            mri_info_visitid    mri_info_manufacturer  \
0  P023_INV0AU5R8NA_20170817  Philips Medical Systems   
1  S086_INV0CP9XGTP_20170526                  SIEMENS   
2  S014_INV0CZBUV4C_20170707                  SIEMENS   
3  P043_INV0EWGP0U5_20170721  Philips Medical Systems   
4  P043_INV0F82C6R8_20170805  Philips Medical Systems   

  mri_info_manufacturersmn mri_info_deviceserialnumber  \
0                  Ingenia                       42376   
1               Prisma_fit                      167021   
2                   Prisma                       66105   
3          Achieva dStream                       17366   
4          Achieva dStream                       17366   

   mri_info_magneticfieldstrength mri_info_softwareversion  
0                             3.0            5.3.0\5.3.0.0  
1                             3.0             syngo MR E11  
2                             3.0             syngo MR E11  
3                             3.0            5.3.0\5.3.0.3  
4                             3.0            5.3.0\5.3.0.3

## Assemble rs-fMRI dataframe

In [15]:
# Between network table
bn_t, bn_l = load_abcd_table(abcd_table_path + 'abcd_betnet02.txt')
# Network to subcortical table
ns_t, ns_l = load_abcd_table(abcd_table_path + 'mrirscor02.txt')
# See which columns are in both tables
bn_l.loc[bn_l.doc.isin(ns_l.doc),:]

name  \
0                                       collection_id   
2                                          dataset_id   
3                                          subjectkey   
4                                      src_subject_id   
5                                      interview_date   
6                                       interview_age   
7                                              gender   
8                                           eventname   
9                   rsfmri_cor_network.gordon_visitid   
10                       rsfmri_cor_network.gordon_tr   
11                   rsfmri_cor_network.gordon_numtrs   
12                    rsfmri_cor_network.gordon_nvols   
13          rsfmri_cor_network.gordon_subthresh.nvols   
14   rsfmri_cor_network.gordon_subthresh.contig.nvols   
15                 rsfmri_cor_network.gordon_ntpoints   
16              rsfmri_cor_network.gordon_mean.motion   
17               rsfmri_cor_network.gordon_max.motion   
18               rsfmri_cor_network.gordon_mean.trans   
19                rsfmri_cor_network.gordon_max.trans   
20                 rsfmri_cor_network.gordon_mean.rot   
21                  rsfmri_cor_network.gordon_max.rot   
191                                  collection_title   
192                               promoted_subjectkey   
193                                 study_cohort_name   

                                                                                                 doc  
0                                                                                      collection_id  
2                                                                                         dataset_id  
3                                      The NDAR Global Unique Identifier (GUID) for research subject  
4                                                         Subject ID how it's defined in lab/project  
5    Date on which the interview/genetic test/sampling/imaging/biospecimen was completed. MM/DD/YYYY  
6                                  Age in months at the time of the interview/test/sampling/imaging.  
7                                                                                 Sex of the subject  
8                                                    The event name for which the data was collected  
9                                                                                         Visit name  
10                                                                  Pulse repetition time in seconds  
11                                                                   Number of frames in acquisition  
12                                                      Number of frames after removing dummy frames  
13                                                                    Number of frames with FD < 0.2  
14                  Number of frames with FD < 0.2 and at least 5 contiguous, supra-threshold frames  
15         Number of frames after excluding outlier frames (based on standard deviation across ROIs)  
16                                                              Average framewise displacement in mm  
17                                                              Maximum framewise displacement in mm  
18                                                               Average framewise translation in mm  
19                                                               Maximum framewise translation in mm  
20                                                             Average framewise rotation in radians  
21                                                             Maximum framewise rotation in radians  
191                                                                                 collection_title  
192                                                                              promoted_subjectkey  
193                                                                                study_cohort_name

In [16]:
# We'll merge on subjectkey and interview_date, filter out the other columns from ns_t before merging
ns_t.drop(ns_l.loc[ns_l.doc.isin(bn_l.doc),'name'].drop([3,5]).values,
          axis=1,
          inplace=True)

con = bn_t.merge(ns_t,
                 how='outer',
                 on=['subjectkey','interview_date'])

con_l = pd.concat([bn_l, 
                   ns_l[~ns_l.name.isin(bn_l.loc[bn_l.doc.isin(ns_l.doc),'name'].values)]]).reset_index(drop=True)

In [17]:
# Merge in balancing variables
con = con.merge(for_balancing.loc[:,['subjectkey','eventname','ehi_ss_score']], how='left',
          on=['subjectkey','eventname'], indicator=True)

con_l = con_l.append(pd.DataFrame([{'name':'ehi_ss_score','doc':'Handedness score rating'}]))

/data/nielsond/python/envs/py3_c/lib/python3.6/site-packages/pandas/core/frame.py:6211: FutureWarning: Sorting because non-concatenation axis is not aligned. A future version
of pandas will change to not sort by default.

To accept the future behavior, pass 'sort=False'.

To retain the current behavior and silence the warning, pass 'sort=True'.

  sort=sort)


In [24]:
con.groupby(['_merge'])[['subjectkey']].count()
con.drop('_merge', 1, inplace=True)

subjectkey
_merge                
left_only            0
right_only           0
both              4521

In [19]:
con.columns

Index(['collection_id', 'abcd_betnet02_id', 'dataset_id', 'subjectkey',
       'src_subject_id', 'interview_date', 'interview_age', 'gender',
       'eventname', 'rsfmri_cor_network.gordon_visitid',
       ...
       'rsfmri_cor_network.gordon_visual_subcort.aseg_thalamus.proper.rh',
       'rsfmri_cor_network.gordon_visual_subcort.aseg_caudate.rh',
       'rsfmri_cor_network.gordon_visual_subcort.aseg_putamen.rh',
       'rsfmri_cor_network.gordon_visual_subcort.aseg_pallidum.rh',
       'rsfmri_cor_network.gordon_visual_subcort.aseg_hippocampus.rh',
       'rsfmri_cor_network.gordon_visual_subcort.aseg_amygdala.rh',
       'rsfmri_cor_network.gordon_visual_subcort.aseg_accumbens.area.rh',
       'rsfmri_cor_network.gordon_visual_subcort.aseg_ventraldc.rh',
       'ehi_ss_score', '_merge'],
      dtype='object', length=444)

In [20]:
# Get a list of Metric columns
con_meta_cols = ['collection_id', 'dataset_id', 'subjectkey',
            'src_subject_id', 'interview_date', 'interview_age',
            'gender', 'event_name', 'visit', 'rsfm_tr', 'eventname',
            'rsfm_nreps', 'rsfm_numtrs', 'pipeline_version',  'scanner_manufacturer_pd',
            'scanner_type_pd','deviceserialnumber', 'magnetic_field_strength',
            'procdate', 'collection_title', 'promoted_subjectkey',
            'study_cohort_name','ehi_ss_scoreb', 'qc_ok']
con_metric_cols = con_l.loc[~con_l.name.isin(con_meta_cols), 'name'].values


# pull out the roi and network names 

con_l['from_network'] = con_l.loc[con_l.name.isin(con_metric_cols),'doc'].str.split('between ').str[1].str.split('network').str[0]
con_l['to'] = con_l.loc[con_l.name.isin(con_metric_cols),'doc'].str.split('between ').str[1].str.split('network').str[1].str.split(' and').str[1].str.replace('ASEG ROI', '')
con_l['roi'] = con_l.loc[con_l.name.isin(con_metric_cols),'doc'].str.split('and ASEG ROI').str[1].str.strip()

con_l['from_network'].unique()
con_l.roi.unique()

array([nan, 'auditory ', 'cingulo-opercular ', 'cingulo-parietal ',
       'default ', 'dorsal attention ', 'fronto-parietal ', '"none" ',
       'retrosplenial temporal ', 'sensorimotor hand ',
       'sensorimotor mouth ', 'salience ', 'ventral attention ',
       'visual '], dtype=object)

array([nan, 'left-cerebellum-cortex', 'left-thalamus-proper',
       'left-caudate', 'left-putamen', 'left-pallidum', 'brain-stem',
       'left-hippocampus', 'left-amygdala', 'left-accumbens-area',
       'left-ventraldc', 'right-cerebellum-cortex',
       'right-thalamus-proper', 'right-caudate', 'right-putamen',
       'right-pallidum', 'right-hippocampus', 'right-amygdala',
       'right-accumbens-area', 'right-ventraldc'], dtype=object)

In [21]:
con_l

doc  \
0                                                                                      collection_id   
1                                                                                   abcd_betnet02_id   
2                                                                                         dataset_id   
3                                      The NDAR Global Unique Identifier (GUID) for research subject   
4                                                         Subject ID how it's defined in lab/project   
5    Date on which the interview/genetic test/sampling/imaging/biospecimen was completed. MM/DD/YYYY   
6                                  Age in months at the time of the interview/test/sampling/imaging.   
7                                                                                 Sex of the subject   
8                                                    The event name for which the data was collected   
9                                                                                         Visit name   
10                                                                  Pulse repetition time in seconds   
11                                                                   Number of frames in acquisition   
12                                                      Number of frames after removing dummy frames   
13                                                                    Number of frames with FD < 0.2   
14                  Number of frames with FD < 0.2 and at least 5 contiguous, supra-threshold frames   
15         Number of frames after excluding outlier frames (based on standard deviation across ROIs)   
16                                                              Average framewise displacement in mm   
17                                                              Maximum framewise displacement in mm   
18                                                               Average framewise translation in mm   
19                                                               Maximum framewise translation in mm   
20                                                             Average framewise rotation in radians   
21                                                             Maximum framewise rotation in radians   
22                                 Average correlation between auditory network and auditory network   
23                        Average correlation between auditory network and cingulo-opercular network   
24                         Average correlation between auditory network and cingulo-parietal network   
25                                  Average correlation between auditory network and default network   
26                         Average correlation between auditory network and dorsal attention network   
27                          Average correlation between auditory network and fronto-parietal network   
28                                   Average correlation between auditory network and "none" network   
29                   Average correlation between auditory network and retrosplenial temporal network   
30                        Average correlation between auditory network and sensorimotor hand network   
31                       Average correlation between auditory network and sensorimotor mouth network   
32                                 Average correlation between auditory network and salience network   
33                        Average correlation between auditory network and ventral attention network   
34                                   Average correlation between auditory network and visual network   
35                        Average correlation between cingulo-opercular network and auditory network   
36               Average correlation between cingulo-opercular network and cingulo-opercular network   
37                Average correlation between cingulo-opercular network and cingulo-parietal network   
38                         Average correl

In [25]:
con.head()

collection_id  abcd_betnet02_id  dataset_id        subjectkey  \
0           2573             20285       17007  NDAR_INVFAFNLCWD   
1           2573             19693       17007  NDAR_INVB1DNH7JC   
2           2573             20348       17007  NDAR_INVFPFM6B57   
3           2573             19414       17007  NDAR_INV96KLPLFJ   
4           2573             19933       17007  NDAR_INVCW8WDA3J   

     src_subject_id interview_date  interview_age gender  \
0  NDAR_INVFAFNLCWD     05/08/2017            108      F   
1  NDAR_INVB1DNH7JC     12/09/2016            121      F   
2  NDAR_INVFPFM6B57     03/02/2017            108      M   
3  NDAR_INV96KLPLFJ     07/21/2017            109      M   
4  NDAR_INVCW8WDA3J     03/31/2017            116      M   

               eventname rsfmri_cor_network.gordon_visitid  \
0  baseline_year_1_arm_1         S014_INVFAFNLCWD_20170509   
1  baseline_year_1_arm_1         S053_INVB1DNH7JC_20161211   
2  baseline_year_1_arm_1         S053_INVFPFM6B57_20170305   
3  baseline_year_1_arm_1         S011_INV96KLPLFJ_20170731   
4  baseline_year_1_arm_1         S014_INVCW8WDA3J_20170401   

   rsfmri_cor_network.gordon_tr  rsfmri_cor_network.gordon_numtrs  \
0                           0.8                            1532.0   
1                           0.8                            1532.0   
2                           0.8                            1532.0   
3                           0.8                            1532.0   
4                           0.8                            1532.0   

   rsfmri_cor_network.gordon_nvols  rsfmri_cor_network.gordon_subthresh.nvols  \
0                           1500.0                                     1330.0   
1                           1500.0                                     1485.0   
2                           1500.0                                      958.0   
3                           1500.0                                      410.0   
4                           1500.0                                     1475.0   

   rsfmri_cor_network.gordon_subthresh.contig.nvols  \
0                                            1276.0   
1                                            1485.0   
2                                             768.0   
3                                             292.0   
4                                            1471.0   

   rsfmri_cor_network.gordon_ntpoints  rsfmri_cor_network.gordon_mean.motion  \
0                              1155.0                               0.129892   
1                              1377.0                               0.059886   
2                               603.0                               0.332657   
3                               105.0                               1.396390   
4                              1387.0                               0.071670   

   rsfmri_cor_network.gordon_max.motion  rsfmri_cor_network.gordon_mean.trans  \
0                              5.069193                              0.079314   
1                              0.766362                              0.039253   
2                              9.797004                              0.158036   
3                             13.092856                              0.625400   
4                              3.325154                              0.050000   

   rsfmri_cor_network.gordon_max.trans  rsfmri_cor_network.gordon_mean.rot  \
0                             2.522730                            0.050578   
1                             0.242272                            0.020633   
2                             8.979014                            0.174621   
3                             9.843847                            0.770990   
4                             1.256487                            0.021669   

   rsfmri_cor_network.gordon_max.rot  \
0                           2.621751   
1                           0.633536   
2                           3.525160   
3                           8.

## Assemble task based tables

### Tstats

In [87]:
# Load Monetary Incentive Delay data
mid_paths = ['tstgodp101','tstgodp201','tstgodp301', 'tstgodp401']
mid_paths = [abcd_table_path + pp + '.txt' for pp in mid_paths]

mid_contrasts = ['MID anticipation of reward versus neutral',
       'MID anticipation of loss versus neutral',
       'MID reward positive versus negative feeback',
       'MID loss positive versus negative feedback',
       'MID anticipation of large reward versus neutral',
       'MID anticipation of small reward versus neutral',
       'MID anticipation of large versus small reward',
       'MID anticipation of large loss versus neutral',
       'MID anticipation of small loss versus neutral',
       'MID anticipation of small versus large loss']

mid_t_melt, mid_l = load_task_melt_contrasts(mid_paths, mid_contrasts, 'mid')

# Load Stop Signal Task

sst_paths = ['ssttstatp101','ssttstatp201', 'ssttstatp301']
sst_paths = [abcd_table_path + pp + '.txt' for pp in sst_paths]

sst_contrasts = ['SST correct go versus fixation',
       'SST correct stop versus correct go',
       'SST incorrect stop versus correct go',
       'SST any stop versus correct go',
       'SST correct stop versus incorrect stop',
       'SST incorrect go versus correct go',
       'SST incorrect go versus incorrect stop']

sst_t_melt, sst_l = load_task_melt_contrasts(sst_paths, sst_contrasts, 'sst')


nb_paths = ['nbacktstatp101','nbacktstatp201', 'nbacktstatp301', 'nbacktstatp401']
nb_paths = [abcd_table_path + pp+'.txt' for pp in nb_paths]

nb_contrasts = ['nBack 0 back condition', 'nBack 2 back condition',
       'nBack place condition',
       'nBack emotion condition',
       'nBack 2 back versus 0 back contrast',
       'nBack face versus place contrast',
       'nBack emotion versus neutral face contrast',
       'nBack negative face versus positive face contrast',
       'nBack positive face versus neutral face contrast']

nb_t_melt, nb_l = load_task_melt_contrasts(nb_paths, nb_contrasts, 'nb')


/data/nielsond/python/envs/py3_c/lib/python3.6/site-packages/ipykernel_launcher.py:75: FutureWarning: Sorting because non-concatenation axis is not aligned. A future version
of pandas will change to not sort by default.

To accept the future behavior, pass 'sort=False'.

To retain the current behavior and silence the warning, pass 'sort=True'.



In [88]:
tb_t = pd.concat([mid_t_melt, sst_t_melt, nb_t_melt])
tb_t = tb_t.merge(for_balancing.loc[:,['subjectkey','eventname','ehi_y_ss_scoreb','scanner_manufacturer_pd',
            'scanner_type_pd', 'deviceserialnumber']],
                  how='left',
                  on=['subjectkey','eventname'])

/data/nielsond/python/envs/py3_c/lib/python3.6/site-packages/ipykernel_launcher.py:1: FutureWarning: Sorting because non-concatenation axis is not aligned. A future version
of pandas will change to not sort by default.

To accept the future behavior, pass 'sort=False'.

To retain the current behavior and silence the warning, pass 'sort=True'.

  """Entry point for launching an IPython kernel.
/data/nielsond/python/envs/py3_c/lib/python3.6/site-packages/pandas/core/indexing.py:1472: FutureWarning: 
Passing list-likes to .loc or [] with any missing label will raise
KeyError in the future, you can use .reindex() as an alternative.

See the documentation here:
https://pandas.pydata.org/pandas-docs/stable/indexing.html#deprecate-loc-reindex-listlike
  return self._getitem_tuple(key)


In [89]:
tb_t.head()

collection_id                                     collection_title  \
0           2573  Adolescent Brain Cognitive Development Study (ABCD)   
1           2573  Adolescent Brain Cognitive Development Study (ABCD)   
2           2573  Adolescent Brain Cognitive Development Study (ABCD)   
3           2573  Adolescent Brain Cognitive Development Study (ABCD)   
4           2573  Adolescent Brain Cognitive Development Study (ABCD)   

                                    contrast  dataset_id  \
0  MID anticipation of reward versus neutral       14688   
1  MID anticipation of reward versus neutral       14688   
2  MID anticipation of reward versus neutral       14688   
3  MID anticipation of reward versus neutral       14688   
4  MID anticipation of reward versus neutral       14688   

               eventname  fmri_beta_gparc_mean_motion  fmri_beta_gparc_numtrs  \
0  baseline_year_1_arm_1                     0.248041                     822   
1  baseline_year_1_arm_1                     0.182486                     822   
2  baseline_year_1_arm_1                     0.190756                     822   
3  baseline_year_1_arm_1                     0.114147                     816   
4  baseline_year_1_arm_1                     0.266772                     816   

   fmri_beta_gparc_tr gender  interview_age interview_date     lhgp1  \
0                 0.8      M            130     08/22/2017 -0.937017   
1                 0.8      F            118     03/21/2017 -0.192616   
2                 0.8      F            130     05/12/2017  0.098063   
3                 0.8      F            118     02/26/2017  0.425078   
4                 0.8      F            124     07/08/2017  0.289284   

     lhgp10   lhgp100   lhgp101   lhgp102   lhgp103   lhgp104   lhgp105  \
0 -0.591043 -0.519616 -0.671567 -0.240438 -0.435169 -0.070034 -0.459225   
1  0.637961  0.148675  0.094617  0.269034  0.553313  0.593500  0.162627   
2  0.022595 -0.036413 -0.500000 -0.146195  0.083582  0.402497  0.000902   
3 -0.276923  0.037081 -0.139792 -0.535822 -0.174595 -0.110404  0.097908   
4  0.014388  0.251693  0.387506  0.247266  0.092138  0.051646  0.235468   

    lhgp106   lhgp107   lhgp108   lhgp109    lhgp11   lhgp110   lhgp111  \
0  0.071072 -0.388493  0.261926  0.001841 -0.292160  0.320073 -0.532535   
1  0.431113  0.302162  0.125768  0.664408  0.232657  0.443311 -0.188599   
2  0.322008  0.043152  0.351209  0.211560 -0.288753  0.500303  0.181679   
3  0.373499  0.535321 -0.121898  0.227695 -0.207566  0.484702 -0.228007   
4 -0.219911  0.669151  0.489779  0.345701 -0.157411 -0.042023  0.147266   

    lhgp112   lhgp113   lhgp114   lhgp115   lhgp116   lhgp117   lhgp118  \
0  0.469769 -0.045275  0.182136  0.329423 -0.178648 -0.562087  0.017274   
1  0.281406  0.046891 -0.399507  0.190195 -0.132623 -0.078386 -0.210112   
2 -0.185635  0.483441  0.854668  0.441618  0.598791  0.418621 -0.130590   
3 -0.091394 -0.167711 -0.045245 -0.583172 -0.021108 -0.012753 -0.045808   
4 -0.016314  0.450529 -0.973966  0.675421  0.688804  0.207965 -0.039087   

    lhgp119    lhgp12   lhgp120   lhgp121   lhgp122   lhgp123   lhgp124  \
0 -0.607081 -0.069953  0.010518  0.378842  0.050593  0.780789 -0.314452   
1 -0.610402  0.240185 -0.217960 -0.487563 -0.208487  0.232487  0.052339   
2  0.408090 -0.548231 -0.068376  0.454149  0.069465 -0.161991 -0.304982   
3  0.366184  0.247886  0.325711  0.042617 -0.366057  0.514702 -0.504630   
4  0.369307  0.128680  0.495773  0.885444 -0.235301  0.305891 -0.418691   

    lhgp125   lhgp126   lhgp127   lhgp128   lhgp129    lhgp13   lhgp130  \
0  0.212822  0.261555 -0.414366 -0.152603 -0.687435 -0.449778 -0.665823   
1 -0.158725 -0.082216 -0.161646  0.216963  0.143788  0.482159  0.026598   
2 -0.136095  0.278063  0.185069  0.105266  0.073657 -0.444219 -0.171802   
3  0.150277  0.041494  0.210423  0.349502 -0.192654 -0.319192 -0.421959   
4  0.202873  0.054594  0.110759  0.055756 -0.106923  0.026839 -0.077018   

    lhgp131   lhgp132   lhgp

### Betas

In [88]:
mid_t, mid_l = load_abcd_table(abcd_table_path + 'midaparc02.txt')
pd.unique(mid_l.doc.str.split('in ASEG').str[0])

array(['collection_id', 'midaparc02_id', 'dataset_id',
       'The NDAR Global Unique Identifier (GUID) for research subject',
       "Subject ID how it's defined in lab/project",
       'Date on which the interview/genetic test/sampling/imaging/biospecimen was completed. MM/DD/YYYY',
       'Age in months at the time of the interview/test/sampling/imaging.',
       'Sex of the subject',
       'The event name for which the data was collected', 'Visit name',
       'Pulse repetition time in seconds',
       'Number of frames in acquisition', 'Degrees of freedom',
       'Number of frames after removing dummy frames',
       'Number of frames with FD < 0.2',
       'Average framewise displacement in mm',
       'Maximum framewise displacement in mm',
       'Average framewise translation in mm',
       'Maximum framewise translation in mm',
       'Average framewise rotation in radians',
       'Maximum framewise rotation in radians',
       'Mean beta weight for MID anticipation of rew

In [103]:
fn='midaparcp202'
mid_t, mid_l = load_abcd_table(abcd_table_path + f'{fn}.txt')
pd.unique(mid_l.doc.str.split('in APARC').str[0])

array(['collection_id', 'midaparcp202_id', 'dataset_id',
       'The NDAR Global Unique Identifier (GUID) for research subject',
       "Subject ID how it's defined in lab/project",
       'Date on which the interview/genetic test/sampling/imaging/biospecimen was completed. MM/DD/YYYY',
       'Age in months at the time of the interview/test/sampling/imaging.',
       'Sex of the subject',
       'The event name for which the data was collected',
       'Mean beta weight for MID anticipation of reward versus neutral contrast ',
       'Mean beta weight for MID anticipation of loss versus neutral contrast ',
       'Mean beta weight for MID reward positive versus negative feedback contrast ',
       'Mean beta weight for MID loss positive versus negative feedback contrast ',
       'Mean beta weight for MID anticipation of large reward versus neutral contrast ',
       'Mean beta weight for MID anticipation of small reward versus neutral contrast ',
       'Mean beta weight for MID anti

In [105]:
mid_l

name  \
0                     collection_id   
1                   midaparcp202_id   
2                        dataset_id   
3                        subjectkey   
4                    src_subject_id   
5                    interview_date   
6                     interview_age   
7                            gender   
8                         eventname   
9       tfmri_ma_alvsl_b_scs_vtdcrh   
10        tfmri_ma_arvn_b_cds_bkslh   
11    tfmri_ma_arvn_b_cds_clatcgelh   
12     tfmri_ma_arvn_b_cds_clmdfrlh   
13         tfmri_ma_arvn_b_cds_culh   
14     tfmri_ma_arvn_b_cds_ehinallh   
15         tfmri_ma_arvn_b_cds_fflh   
16       tfmri_ma_arvn_b_cds_ifpalh   
17       tfmri_ma_arvn_b_cds_iftplh   
18      tfmri_ma_arvn_b_cds_ihcgelh   
19        tfmri_ma_arvn_b_cds_loclh   
20     tfmri_ma_arvn_b_cds_lobofrlh   
21         tfmri_ma_arvn_b_cds_lglh   
22     tfmri_ma_arvn_b_cds_mobofrlh   
23       tfmri_ma_arvn_b_cds_mdtplh   
24      tfmri_ma_arvn_b_cds_phpallh   
25        tfmri_ma_arvn_b_cds_pctlh   
26        tfmri_ma_arvn_b_cds_ppclh   
27     tfmri_ma_arvn_b_cds_pbalislh   
28      tfmri_ma_arvn_b_cds_prgislh   
29        tfmri_ma_arvn_b_cds_pcelh   
30      tfmri_ma_arvn_b_cds_postclh   
31      tfmri_ma_arvn_b_cds_pocgelh   
32       tfmri_ma_arvn_b_cds_preclh   
33         tfmri_ma_arvn_b_cds_pulh   
34    tfmri_ma_arvn_b_cds_roatcgelh   
35     tfmri_ma_arvn_b_cds_romdfrlh   
36       tfmri_ma_arvn_b_cds_sufrlh   
37       tfmri_ma_arvn_b_cds_supalh   
38       tfmri_ma_arvn_b_cds_sutplh   
39        tfmri_ma_arvn_b_cds_smglh   
40     tfmri_ma_arvn_b_cds_frpolelh   
41     tfmri_ma_arvn_b_cds_tppolelh   
42       tfmri_ma_arvn_b_cds_tvtplh   
43     tfmri_ma_arvn_b_cds_insulalh   
44        tfmri_ma_arvn_b_cds_bksrh   
45    tfmri_ma_arvn_b_cds_clatcgerh   
46     tfmri_ma_arvn_b_cds_clmdfrrh   
47         tfmri_ma_arvn_b_cds_curh   
48     tfmri_ma_arvn_b_cds_ehinalrh   
49         tfmri_ma_arvn_b_cds_ffrh   
50       tfmri_ma_arvn_b_cds_ifparh   
51       tfmri_ma_arvn_b_cds_iftprh   
52      tfmri_ma_arvn_b_cds_ihcgerh   
53        tfmri_ma_arvn_b_cds_locrh   
54     tfmri_ma_arvn_b_cds_lobofrrh   
55         tfmri_ma_arvn_b_cds_lgrh   
56     tfmri_ma_arvn_b_cds_mobofrrh   
57       tfmri_ma_arvn_b_cds_mdtprh   
58      tfmri_ma_arvn_b_cds_phpalrh   
59        tfmri_ma_arvn_b_cds_pctrh   
60        tfmri_ma_arvn_b_cds_ppcrh   
61     tfmri_ma_arvn_b_cds_pbalisrh   
62      tfmri_ma_arvn_b_cds_prgisrh   
63        tfmri_ma_arvn_b_cds_pcerh   
64      tfmri_ma_arvn_b_cds_postcrh   
65      tfmri_ma_arvn_b_cds_pocgerh   
66       tfmri_ma_arvn_b_cds_precrh   
67         tfmri_ma_arvn_b_cds_purh   
68    tfmri_ma_arvn_b_cds_roatcgerh   
69     tfmri_ma_arvn_b_cds_romdfrrh   
70       tfmri_ma_arvn_b_cds_sufrrh   
71       tfmri_ma_arvn_b_cds_suparh   
72       tfmri_ma_arvn_b_cds_sutprh   
73        tfmri_ma_arvn_b_cds_smgrh   
74     tfmri_ma_arvn_b_cds_frpolerh   
75     tfmri_ma_arvn_b_cds_tppolerh   
76       tfmri_ma_arvn_b_cds_tvtprh   
77     tfmri_ma_arvn_b_cds_insularh   
78        tfmri_ma_acvn_b_cds_bkslh   
79    tfmri_ma_acvn_b_cds_clatcgelh   
80     tfmri_ma_acvn_b_cds_clmdfrlh   
81         tfmri_ma_acvn_b_cds_culh   
82     tfmri_ma_acvn_b_cds_ehinallh   
83         tfmri_ma_acvn_b_cds_fflh   
84       tfmri_ma_acvn_b_cds_ifpalh   
85       tfmri_ma_acvn_b_cds_iftplh   
86      tfmri_ma_acvn_b_cds_ihcgelh   
87        tfmri_ma_acvn_b_cds_loclh   
88     tfmri_ma_acvn_b_cds_lobofrlh   
89         tfmri_ma_acvn_b_cds_lglh   
90     tfmri_ma_acvn_b_cds_mobofrlh   
91       tfmri_ma_acvn_b_cds_mdtplh   
92      tfmri_ma_acvn_b_cds_phpallh   
93        tfmri_ma_acvn_b_cds_pctlh   
94        tfmri_ma_acvn_b_cds_ppclh   
95     tfmri_ma_acvn_b_cds_pbalislh   
96      tfmri_ma_acvn_b_cds_prgislh   
97        tfmri_ma_acvn_b_cds_pcelh   
98      tfmri_ma_acvn_b_cds_postclh   
99      tfmri_ma_acvn_b_cds_pocgelh   
100      tfmri_ma_acvn_b_cds_preclh   
101        tfmri_ma_acvn_b_cds_pulh   
102   tfmri_ma

In [51]:
fn = 'abcd_midr1bwp101'
mid_t, mid_l = load_abcd_table(abcd_table_path + f'{fn}.txt')
pd.unique(mid_l.doc.str.split('in APARC').str[0].str.split('in ASEG').str[0])
mid_l

array(['collection_id', 'abcd_midr1bwp101_id', 'dataset_id',
       'The NDAR Global Unique Identifier (GUID) for research subject',
       "Subject ID how it's defined in lab/project",
       'Date on which the interview/genetic test/sampling/imaging/biospecimen was completed. MM/DD/YYYY',
       'Age in months at the time of the interview/test/sampling/imaging.',
       'Sex of the subject',
       'The event name for which the data was collected', 'Visit name',
       'Pulse repetition time in seconds',
       'Number of frames in acquisition', 'Degrees of freedom',
       'Number of frames after removing dummy frames',
       'Number of frames with FD < 0.2',
       'Average framewise displacement in mm',
       'Maximum framewise displacement in mm',
       'Average framewise translation in mm',
       'Maximum framewise translation in mm',
       'Average framewise rotation in radians',
       'Maximum framewise rotation in radians',
       'Mean beta weight for MID run 1 anticip

name  \
0                     collection_id   
1               abcd_midr1bwp101_id   
2                        dataset_id   
3                        subjectkey   
4                    src_subject_id   
5                    interview_date   
6                     interview_age   
7                            gender   
8                         eventname   
9       tfmri_mid_run1_beta_visitid   
10           tfmri_mid_run1_beta_tr   
11       tfmri_mid_run1_beta_numtrs   
12          tfmri_mid_run1_beta_dof   
13        tfmri_mid_run1_beta_nvols   
14           tfmri_mr1_beta_stnvols   
15                tfmri_mr1_beta_mm   
16         tfmri_mr1_beta_maxmotion   
17         tfmri_mr1_beta_meantrans   
18     tfmri_mid_run1_beta_maxtrans   
19      tfmri_mid_run1_beta_meanrot   
20       tfmri_mid_run1_beta_maxrot   
21       tfmri_mr1_arvn_bscs_cbwmlh   
22        tfmri_mr1_arvn_bscs_lvelh   
23       tfmri_mr1_arvn_bscs_iftvlh   
24      tfmri_mr1_arvn_bscs_crbwmlh   
25      tfmri_mr1_arvn_bscs_crbcxlh   
26         tfmri_mr1_arvn_bscs_tplh   
27        tfmri_mr1_arvn_bscs_ctelh   
28         tfmri_mr1_arvn_bscs_pulh   
29         tfmri_mr1_arvn_bscs_pdlh   
30     tfmri_mr1_arvn_bscs_3rdvicle   
31     tfmri_mr1_arvn_bscs_4thvicle   
32           tfmri_mr1_arvn_bscs_bs   
33       tfmri_mr1_arvn_bscs_hpuslh   
34         tfmri_mr1_arvn_bscs_aylh   
35          tfmri_mr1_arvn_bscs_csf   
36         tfmri_mr1_arvn_bscs_aalh   
37       tfmri_mr1_arvn_bscs_vtdclh   
38       tfmri_mr1_arvn_bscs_cbwmrh   
39        tfmri_mr1_arvn_bscs_lverh   
40        tfmri_mr1_arvn_bscs_iftvh   
41      tfmri_mr1_arvn_bscs_crbwmrh   
42      tfmri_mr1_arvn_bscs_crbcxrh   
43         tfmri_mr1_arvn_bscs_tprh   
44        tfmri_mr1_arvn_bscs_cterh   
45         tfmri_mr1_arvn_bscs_purh   
46         tfmri_mr1_arvn_bscs_pdrh   
47       tfmri_mr1_arvn_bscs_hpusrh   
48         tfmri_mr1_arvn_bscs_ayrh   
49         tfmri_mr1_arvn_bscs_aarh   
50       tfmri_mr1_arvn_bscs_vtdcrh   
51       tfmri_mr1_alvn_bscs_cbwmlh   
52        tfmri_mr1_alvn_bscs_lvelh   
53       tfmri_mr1_alvn_bscs_iftvlh   
54      tfmri_mr1_alvn_bscs_crbwmlh   
55      tfmri_mr1_alvn_bscs_crbcxlh   
56         tfmri_mr1_alvn_bscs_tplh   
57        tfmri_mr1_alvn_bscs_ctelh   
58         tfmri_mr1_alvn_bscs_pulh   
59         tfmri_mr1_alvn_bscs_pdlh   
60     tfmri_mr1_alvn_bscs_3rdvicle   
61     tfmri_mr1_alvn_bscs_4thvicle   
62           tfmri_mr1_alvn_bscs_bs   
63       tfmri_mr1_alvn_bscs_hpuslh   
64         tfmri_mr1_alvn_bscs_aylh   
65          tfmri_mr1_alvn_bscs_csf   
66         tfmri_mr1_alvn_bscs_aalh   
67       tfmri_mr1_alvn_bscs_vtdclh   
68       tfmri_mr1_alvn_bscs_cbwmrh   
69        tfmri_mr1_alvn_bscs_lverh   
70        tfmri_mr1_alvn_bscs_iftvh   
71      tfmri_mr1_alvn_bscs_crbwmrh   
72      tfmri_mr1_alvn_bscs_crbcxrh   
73         tfmri_mr1_alvn_bscs_tprh   
74        tfmri_mr1_alvn_bscs_cterh   
75         tfmri_mr1_alvn_bscs_purh   
76         tfmri_mr1_alvn_bscs_pdrh   
77       tfmri_mr1_alvn_bscs_hpusrh   
78         tfmri_mr1_alvn_bscs_ayrh   
79         tfmri_mr1_alvn_bscs_aarh   
80       tfmri_mr1_alvn_bscs_vtdcrh   
81     tfmri_mr1_rpvnfb_bscs_cbwmlh   
82      tfmri_mr1_rpvnfb_bscs_lvelh   
83     tfmri_mr1_rpvnfb_bscs_iftvlh   
84    tfmri_mr1_rpvnfb_bscs_crbwmlh   
85    tfmri_mr1_rpvnfb_bscs_crbcxlh   
86       tfmri_mr1_rpvnfb_bscs_tplh   
87      tfmri_mr1_rpvnfb_bscs_ctelh   
88       tfmri_mr1_rpvnfb_bscs_pulh   
89       tfmri_mr1_rpvnfb_bscs_pdlh   
90   tfmri_mr1_rpvnfb_bscs_3rdvicle   
91   tfmri_mr1_rpvnfb_bscs_4thvicle   
92         tfmri_mr1_rpvnfb_bscs_bs   
93     tfmri_mr1_rpvnfb_bscs_hpuslh   
94       tfmri_mr1_rpvnfb_bscs_aylh   
95        tfmri_mr1_rpvnfb_bscs_csf   
96       tfmri_mr1_rpvnfb_bscs_aalh   
97     tfmri_mr1_rpvnfb_bscs_vtdclh   
98     tfmri_mr1_rpvnfb_bscs_cbwmrh   
99      tfmri_mr1_rpvnfb_bscs_lverh   
100     tfmri_mr1_rpvnfb_bscs_iftvh   
101   tfmri_mr1_rpvnfb_bscs_crbwmrh   
102   tfmri_mr

In [52]:
fn = 'abcd_midr1bwp201'
mid_t, mid_l = load_abcd_table(abcd_table_path + f'{fn}.txt')
pd.unique(mid_l.doc.str.split('in APARC').str[0].str.split('in ASEG').str[0])
mid_l

array(['collection_id', 'abcd_midr1bwp201_id', 'dataset_id',
       'The NDAR Global Unique Identifier (GUID) for research subject',
       "Subject ID how it's defined in lab/project",
       'Date on which the interview/genetic test/sampling/imaging/biospecimen was completed. MM/DD/YYYY',
       'Age in months at the time of the interview/test/sampling/imaging.',
       'Sex of the subject',
       'Mean beta weight for MID run 1 anticipation of reward versus neutral contrast ',
       'Mean beta weight for MID run 1 anticipation of loss versus neutral contrast ',
       'Mean beta weight for MID run 1 reward positive versus negative feedback contrast ',
       'Mean beta weight for MID run 1 loss positive versus negative feedback contrast ',
       'Mean beta weight for MID run 1 anticipation of large reward versus neutral contrast ',
       'Mean beta weight for MID run 1 anticipation of small reward versus neutral contrast ',
       'Mean beta weight for MID run 1 anticipation of 

name  \
0                     collection_id   
1               abcd_midr1bwp201_id   
2                        dataset_id   
3                        subjectkey   
4                    src_subject_id   
5                    interview_date   
6                     interview_age   
7                            gender   
8       tfmri_mr1_alvsl_bscs_vtdcrh   
9        tfmri_mr1_arvn_bcdk_bstslh   
10     tfmri_mr1_arvn_bcdk_cdatcglh   
11     tfmri_mr1_arvn_bcdk_cdmdftlh   
12         tfmri_mr1_arvn_bcdk_culh   
13     tfmri_mr1_arvn_bcdk_ehinallh   
14         tfmri_mr1_arvn_bcdk_fflh   
15       tfmri_mr1_arvn_bcdk_ifpalh   
16       tfmri_mr1_arvn_bcdk_iftplh   
17       tfmri_mr1_arvn_bcdk_ihcglh   
18      tfmri_mr1_arvn_bcdk_laocclh   
19     tfmri_mr1_arvn_bcdk_laobftlh   
20         tfmri_mr1_arvn_bcdk_lglh   
21      tfmri_mr1_arvn_bcdk_mobftlh   
22       tfmri_mr1_arvn_bcdk_mdtplh   
23     tfmri_mr1_arvn_bcdk_pahpallh   
24       tfmri_mr1_arvn_bcdk_pacnlh   
25    tfmri_mr1_arvn_bcdk_psoprcslh   
26       tfmri_mr1_arvn_bcdk_psoblh   
27       tfmri_mr1_arvn_bcdk_pstglh   
28         tfmri_mr1_arvn_bcdk_pclh   
29     tfmri_mr1_arvn_bcdk_postcnlh   
30      tfmri_mr1_arvn_bcdk_pstcglh   
31      tfmri_mr1_arvn_bcdk_precnlh   
32        tfmri_mr1_arvn_bcdk_pculh   
33      tfmri_mr1_arvn_bcdk_ratcglh   
34      tfmri_mr1_arvn_bcdk_rmdftlh   
35       tfmri_mr1_arvn_bcdk_suftlh   
36       tfmri_mr1_arvn_bcdk_supalh   
37       tfmri_mr1_arvn_bcdk_sutplh   
38         tfmri_mr1_arvn_bcdk_smlh   
39     tfmri_mr1_arvn_bcdk_ftpolelh   
40     tfmri_mr1_arvn_bcdk_tppolelh   
41       tfmri_mr1_arvn_bcdk_tvtplh   
42        tfmri_mr1_arvn_bcdk_ilalh   
43       tfmri_mr1_arvn_bcdk_bstsrh   
44     tfmri_mr1_arvn_bcdk_cdatcgrh   
45     tfmri_mr1_arvn_bcdk_cdmdftrh   
46         tfmri_mr1_arvn_bcdk_curh   
47     tfmri_mr1_arvn_bcdk_ehinalrh   
48         tfmri_mr1_arvn_bcdk_ffrh   
49       tfmri_mr1_arvn_bcdk_ifparh   
50       tfmri_mr1_arvn_bcdk_iftprh   
51       tfmri_mr1_arvn_bcdk_ihcgrh   
52      tfmri_mr1_arvn_bcdk_laoccrh   
53     tfmri_mr1_arvn_bcdk_laobftrh   
54         tfmri_mr1_arvn_bcdk_lgrh   
55      tfmri_mr1_arvn_bcdk_mobftrh   
56       tfmri_mr1_arvn_bcdk_mdtprh   
57     tfmri_mr1_arvn_bcdk_pahpalrh   
58       tfmri_mr1_arvn_bcdk_pacnrh   
59    tfmri_mr1_arvn_bcdk_psoprcsrh   
60       tfmri_mr1_arvn_bcdk_psobrh   
61       tfmri_mr1_arvn_bcdk_pstgrh   
62         tfmri_mr1_arvn_bcdk_pcrh   
63     tfmri_mr1_arvn_bcdk_postcnrh   
64      tfmri_mr1_arvn_bcdk_pstcgrh   
65      tfmri_mr1_arvn_bcdk_precnrh   
66        tfmri_mr1_arvn_bcdk_pcurh   
67      tfmri_mr1_arvn_bcdk_ratcgrh   
68      tfmri_mr1_arvn_bcdk_rmdftrh   
69       tfmri_mr1_arvn_bcdk_suftrh   
70       tfmri_mr1_arvn_bcdk_suparh   
71       tfmri_mr1_arvn_bcdk_sutprh   
72         tfmri_mr1_arvn_bcdk_smrh   
73     tfmri_mr1_arvn_bcdk_ftpolerh   
74     tfmri_mr1_arvn_bcdk_tppolerh   
75       tfmri_mr1_arvn_bcdk_tvtprh   
76        tfmri_mr1_arvn_bcdk_ilarh   
77       tfmri_mr1_alvn_bcdk_bstslh   
78     tfmri_mr1_alvn_bcdk_cdatcglh   
79     tfmri_mr1_alvn_bcdk_cdmdftlh   
80         tfmri_mr1_alvn_bcdk_culh   
81     tfmri_mr1_alvn_bcdk_ehinallh   
82         tfmri_mr1_alvn_bcdk_fflh   
83       tfmri_mr1_alvn_bcdk_ifpalh   
84       tfmri_mr1_alvn_bcdk_iftplh   
85       tfmri_mr1_alvn_bcdk_ihcglh   
86      tfmri_mr1_alvn_bcdk_laocclh   
87     tfmri_mr1_alvn_bcdk_laobftlh   
88         tfmri_mr1_alvn_bcdk_lglh   
89      tfmri_mr1_alvn_bcdk_mobftlh   
90       tfmri_mr1_alvn_bcdk_mdtplh   
91     tfmri_mr1_alvn_bcdk_pahpallh   
92       tfmri_mr1_alvn_bcdk_pacnlh   
93    tfmri_mr1_alvn_bcdk_psoprcslh   
94       tfmri_mr1_alvn_bcdk_psoblh   
95       tfmri_mr1_alvn_bcdk_pstglh   
96         tfmri_mr1_alvn_bcdk_pclh   
97     tfmri_mr1_alvn_bcdk_postcnlh   
98      tfmri_mr1_alvn_bcdk_pstcglh   
99      tfmri_mr1_alvn_bcdk_precnlh   
100       tfmri_mr1_alvn_bcdk_pculh   
101     tfmri_mr1_alvn_bcdk_ratcglh   
102     tfmri_

In [53]:
fn = 'midr2bwp101'
mid_t, mid_l = load_abcd_table(abcd_table_path + f'{fn}.txt')
pd.unique(mid_l.doc.str.split('in APARC').str[0].str.split('in ASEG').str[0])
mid_l

array(['collection_id', 'midr2bwp101_id', 'dataset_id',
       'The NDAR Global Unique Identifier (GUID) for research subject',
       "Subject ID how it's defined in lab/project",
       'Date on which the interview/genetic test/sampling/imaging/biospecimen was completed. MM/DD/YYYY',
       'Age in months at the time of the interview/test/sampling/imaging.',
       'Sex of the subject', 'Visit name',
       'Pulse repetition time in seconds',
       'Number of frames in acquisition', 'Degrees of freedom',
       'Number of frames after removing dummy frames',
       'Number of frames with FD < 0.2',
       'Average framewise displacement in mm',
       'Maximum framewise displacement in mm',
       'Average framewise translation in mm',
       'Maximum framewise translation in mm',
       'Average framewise rotation in radians',
       'Maximum framewise rotation in radians',
       'Mean beta weight for MID run 2 anticipation of reward versus neutral contrast ',
       'Mean beta we

name  \
0                     collection_id   
1                    midr2bwp101_id   
2                        dataset_id   
3                        subjectkey   
4                    src_subject_id   
5                    interview_date   
6                     interview_age   
7                            gender   
8            tfmri_mr2_beta_visitid   
9                 tfmri_mr2_beta_tr   
10            tfmri_mr2_beta_numtrs   
11               tfmri_mr2_beta_dof   
12             tfmri_mr2_beta_nvols   
13            tfmri_mr2_beta_stvols   
14                tfmri_mr2_beta_mm   
15         tfmri_mr2_beta_maxmotion   
16         tfmri_mr2_beta_meantrans   
17          tfmri_mr2_beta_maxtrans   
18           tfmri_mr2_beta_meanrot   
19            tfmri_mr2_beta_maxrot   
20      tfmri_mr2_arvn_bscs_crbwmlh   
21     tfmri_mr2_arvn_bscs_lvtclelh   
22     tfmri_mr2_arvn_bscs_inftvtlh   
23       tfmri_mr2_arvn_bscs_cbwmlh   
24       tfmri_mr2_arvn_bscs_cbcxlh   
25         tfmri_mr2_arvn_bscs_tplh   
26        tfmri_mr2_arvn_bscs_cdelh   
27         tfmri_mr2_arvn_bscs_pulh   
28         tfmri_mr2_arvn_bscs_pllh   
29     tfmri_mr2_arvn_bscs_3rdvtcle   
30     tfmri_mr2_arvn_bscs_4thvtcle   
31           tfmri_mr2_arvn_bscs_bs   
32       tfmri_mr2_arvn_bscs_hpuslh   
33         tfmri_mr2_arvn_bscs_aglh   
34          tfmri_mr2_arvn_bscs_csf   
35         tfmri_mr2_arvn_bscs_aalh   
36    tfmri_mr2_arvn_bscs_vtraldclh   
37      tfmri_mr2_arvn_bscs_crbwmrh   
38     tfmri_mr2_arvn_bscs_lvtclerh   
39     tfmri_mr2_arvn_bscs_inftvtrh   
40       tfmri_mr2_arvn_bscs_cbwmrh   
41       tfmri_mr2_arvn_bscs_cbcxrh   
42         tfmri_mr2_arvn_bscs_tprh   
43        tfmri_mr2_arvn_bscs_cderh   
44         tfmri_mr2_arvn_bscs_purh   
45         tfmri_mr2_arvn_bscs_plrh   
46       tfmri_mr2_arvn_bscs_hpusrh   
47         tfmri_mr2_arvn_bscs_agrh   
48         tfmri_mr2_arvn_bscs_aarh   
49    tfmri_mr2_arvn_bscs_vtraldcrh   
50      tfmri_mr2_alvn_bscs_crbwmlh   
51     tfmri_mr2_alvn_bscs_lvtclelh   
52     tfmri_mr2_alvn_bscs_inftvtlh   
53       tfmri_mr2_alvn_bscs_cbwmlh   
54       tfmri_mr2_alvn_bscs_cbcxlh   
55         tfmri_mr2_alvn_bscs_tplh   
56        tfmri_mr2_alvn_bscs_cdelh   
57         tfmri_mr2_alvn_bscs_pulh   
58         tfmri_mr2_alvn_bscs_pllh   
59     tfmri_mr2_alvn_bscs_3rdvtcle   
60     tfmri_mr2_alvn_bscs_4thvtcle   
61           tfmri_mr2_alvn_bscs_bs   
62       tfmri_mr2_alvn_bscs_hpuslh   
63         tfmri_mr2_alvn_bscs_aglh   
64          tfmri_mr2_alvn_bscs_csf   
65         tfmri_mr2_alvn_bscs_aalh   
66    tfmri_mr2_alvn_bscs_vtraldclh   
67      tfmri_mr2_alvn_bscs_crbwmrh   
68     tfmri_mr2_alvn_bscs_lvtclerh   
69     tfmri_mr2_alvn_bscs_inftvtrh   
70       tfmri_mr2_alvn_bscs_cbwmrh   
71       tfmri_mr2_alvn_bscs_cbcxrh   
72         tfmri_mr2_alvn_bscs_tprh   
73        tfmri_mr2_alvn_bscs_cderh   
74         tfmri_mr2_alvn_bscs_purh   
75         tfmri_mr2_alvn_bscs_plrh   
76       tfmri_mr2_alvn_bscs_hpusrh   
77         tfmri_mr2_alvn_bscs_agrh   
78         tfmri_mr2_alvn_bscs_aarh   
79    tfmri_mr2_alvn_bscs_vtraldcrh   
80    tfmri_mr2_rpvnfb_bscs_crbwmlh   
81   tfmri_mr2_rpvnfb_bscs_lvtclelh   
82   tfmri_mr2_rpvnfb_bscs_inftvtlh   
83     tfmri_mr2_rpvnfb_bscs_cbwmlh   
84     tfmri_mr2_rpvnfb_bscs_cbcxlh   
85       tfmri_mr2_rpvnfb_bscs_tplh   
86      tfmri_mr2_rpvnfb_bscs_cdelh   
87       tfmri_mr2_rpvnfb_bscs_pulh   
88       tfmri_mr2_rpvnfb_bscs_pllh   
89   tfmri_mr2_rpvnfb_bscs_3rdvtcle   
90   tfmri_mr2_rpvnfb_bscs_4thvtcle   
91         tfmri_mr2_rpvnfb_bscs_bs   
92     tfmri_mr2_rpvnfb_bscs_hpuslh   
93       tfmri_mr2_rpvnfb_bscs_aglh   
94        tfmri_mr2_rpvnfb_bscs_csf   
95       tfmri_mr2_rpvnfb_bscs_aalh   
96    tfmri_mr2_rpvnfb_bscs_vtrdclh   
97    tfmri_mr2_rpvnfb_bscs_crbwmrh   
98   tfmri_mr2_rpvnfb_bscs_lvtclerh   
99   tfmri_mr2_rpvnfb_bscs_inftvtrh   
100    tfmri_mr2_rpvnfb_bscs_cbwmrh   
101    tfmri_mr2_rpvnfb_bscs_cbcxrh   
102      tfmri

In [54]:
fn = 'midr2bwp201'
mid_t, mid_l = load_abcd_table(abcd_table_path + f'{fn}.txt')
pd.unique(mid_l.doc.str.split('in APARC').str[0].str.split('in ASEG').str[0])
mid_l

array(['collection_id', 'midr2bwp201_id', 'dataset_id',
       'The NDAR Global Unique Identifier (GUID) for research subject',
       "Subject ID how it's defined in lab/project",
       'Date on which the interview/genetic test/sampling/imaging/biospecimen was completed. MM/DD/YYYY',
       'Age in months at the time of the interview/test/sampling/imaging.',
       'Sex of the subject',
       'Mean beta weight for MID run 2 anticipation of reward versus neutral contrast ',
       'Mean beta weight for MID run 2 anticipation of loss versus neutral contrast ',
       'Mean beta weight for MID run 2 reward positive versus negative feedback contrast ',
       'Mean beta weight for MID run 2 loss positive versus negative feedback contrast ',
       'Mean beta weight for MID run 2 anticipation of large reward versus neutral contrast ',
       'Mean beta weight for MID run 2 anticipation of small reward versus neutral contrast ',
       'Mean beta weight for MID run 2 anticipation of small

name  \
0                     collection_id   
1                    midr2bwp201_id   
2                        dataset_id   
3                        subjectkey   
4                    src_subject_id   
5                    interview_date   
6                     interview_age   
7                            gender   
8    tfmri_mr2_alvsl_bscs_vtraldcrh   
9        tfmri_mr2_arvn_bcdk_bktslh   
10     tfmri_mr2_arvn_bcdk_clancglh   
11      tfmri_mr2_arvn_bcdk_clmdflh   
12        tfmri_mr2_arvn_bcdk_eculh   
13     tfmri_mr2_arvn_bcdk_ehinallh   
14         tfmri_mr2_arvn_bcdk_fflh   
15       tfmri_mr2_arvn_bcdk_ifpalh   
16       tfmri_mr2_arvn_bcdk_iftplh   
17       tfmri_mr2_arvn_bcdk_ihcglh   
18       tfmri_mr2_arvn_bcdk_locclh   
19      tfmri_mr2_arvn_bcdk_loroflh   
20         tfmri_mr2_arvn_bcdk_lglh   
21      tfmri_mr2_arvn_bcdk_moroflh   
22       tfmri_mr2_arvn_bcdk_mdtplh   
23      tfmri_mr2_arvn_bcdk_phpallh   
24      tfmri_mr2_arvn_bcdk_paraclh   
25      tfmri_mr2_arvn_bcdk_poprclh   
26        tfmri_mr2_arvn_bcdk_poblh   
27    tfmri_mr2_arvn_bcdk_parstrglh   
28        tfmri_mr2_arvn_bcdk_pcnlh   
29      tfmri_mr2_arvn_bcdk_postclh   
30       tfmri_mr2_arvn_bcdk_pocglh   
31       tfmri_mr2_arvn_bcdk_preclh   
32         tfmri_mr2_arvn_bcdk_pclh   
33      tfmri_mr2_arvn_bcdk_rancglh   
34       tfmri_mr2_arvn_bcdk_rmdflh   
35        tfmri_mr2_arvn_bcdk_suflh   
36        tfmri_mr2_arvn_bcdk_spalh   
37       tfmri_mr2_arvn_bcdk_sutplh   
38         tfmri_mr2_arvn_bcdk_smlh   
39      tfmri_mr2_arvn_bcdk_fpolelh   
40     tfmri_mr2_arvn_bcdk_tppolelh   
41      tfmri_mr2_arvn_bcdk_trvtplh   
42        tfmri_mr2_arvn_bcdk_inalh   
43       tfmri_mr2_arvn_bcdk_bktsrh   
44     tfmri_mr2_arvn_bcdk_clancgrh   
45      tfmri_mr2_arvn_bcdk_clmdfrh   
46        tfmri_mr2_arvn_bcdk_ecurh   
47     tfmri_mr2_arvn_bcdk_ehinalrh   
48         tfmri_mr2_arvn_bcdk_ffrh   
49       tfmri_mr2_arvn_bcdk_ifparh   
50       tfmri_mr2_arvn_bcdk_iftprh   
51       tfmri_mr2_arvn_bcdk_ihcgrh   
52       tfmri_mr2_arvn_bcdk_loccrh   
53      tfmri_mr2_arvn_bcdk_lorofrh   
54         tfmri_mr2_arvn_bcdk_lgrh   
55      tfmri_mr2_arvn_bcdk_morofrh   
56       tfmri_mr2_arvn_bcdk_mdtprh   
57      tfmri_mr2_arvn_bcdk_phpalrh   
58      tfmri_mr2_arvn_bcdk_paracrh   
59      tfmri_mr2_arvn_bcdk_poprcrh   
60        tfmri_mr2_arvn_bcdk_pobrh   
61    tfmri_mr2_arvn_bcdk_parstrgrh   
62        tfmri_mr2_arvn_bcdk_pcnrh   
63      tfmri_mr2_arvn_bcdk_postcrh   
64       tfmri_mr2_arvn_bcdk_pocgrh   
65       tfmri_mr2_arvn_bcdk_precrh   
66         tfmri_mr2_arvn_bcdk_pcrh   
67      tfmri_mr2_arvn_bcdk_rancgrh   
68       tfmri_mr2_arvn_bcdk_rmdfrh   
69        tfmri_mr2_arvn_bcdk_sufrh   
70        tfmri_mr2_arvn_bcdk_sparh   
71       tfmri_mr2_arvn_bcdk_sutprh   
72         tfmri_mr2_arvn_bcdk_smrh   
73      tfmri_mr2_arvn_bcdk_fpolerh   
74     tfmri_mr2_arvn_bcdk_tppolerh   
75      tfmri_mr2_arvn_bcdk_trvtprh   
76        tfmri_mr2_arvn_bcdk_inarh   
77       tfmri_mr2_alvn_bcdk_bktslh   
78     tfmri_mr2_alvn_bcdk_clancglh   
79      tfmri_mr2_alvn_bcdk_clmdflh   
80        tfmri_mr2_alvn_bcdk_eculh   
81     tfmri_mr2_alvn_bcdk_ehinallh   
82         tfmri_mr2_alvn_bcdk_fflh   
83       tfmri_mr2_alvn_bcdk_ifpalh   
84       tfmri_mr2_alvn_bcdk_iftplh   
85       tfmri_mr2_alvn_bcdk_ihcglh   
86       tfmri_mr2_alvn_bcdk_locclh   
87      tfmri_mr2_alvn_bcdk_loroflh   
88         tfmri_mr2_alvn_bcdk_lglh   
89      tfmri_mr2_alvn_bcdk_moroflh   
90       tfmri_mr2_alvn_bcdk_mdtplh   
91      tfmri_mr2_alvn_bcdk_phpallh   
92      tfmri_mr2_alvn_bcdk_paraclh   
93      tfmri_mr2_alvn_bcdk_poprclh   
94        tfmri_mr2_alvn_bcdk_poblh   
95    tfmri_mr2_alvn_bcdk_parstrglh   
96        tfmri_mr2_alvn_bcdk_pcnlh   
97      tfmri_mr2_alvn_bcdk_postclh   
98       tfmri_mr2_alvn_bcdk_pocglh   
99       tfmri_mr2_alvn_bcdk_preclh   
100        tfmri_mr2_alvn_bcdk_pclh   
101     tfmri_mr2_alvn_bcdk_rancglh   
102      tfmri

In [55]:
fn = 'mrisstr1bw01'
mid_t, mid_l = load_abcd_table(abcd_table_path + f'{fn}.txt')
pd.unique(mid_l.doc.str.split('in APARC').str[0].str.split('in ASEG').str[0])
mid_l

array(['collection_id', 'mrisstr1bw01_id', 'dataset_id',
       'The NDAR Global Unique Identifier (GUID) for research subject',
       "Subject ID how it's defined in lab/project",
       'Date on which the interview/genetic test/sampling/imaging/biospecimen was completed. MM/DD/YYYY',
       'Age in months at the time of the interview/test/sampling/imaging.',
       'Sex of the subject',
       'The event name for which the data was collected', 'Visit name',
       'Pulse repetition time in seconds',
       'Number of frames in acquisition', 'Degrees of freedom',
       'Number of frames after removing dummy frames',
       'Number of frames with FD < 0.2',
       'Average framewise displacement in mm',
       'Maximum framewise displacement in mm',
       'Average framewise translation in mm',
       'Maximum framewise translation in mm',
       'Average framewise rotation in radians',
       'Maximum framewise rotation in radians',
       'Mean beta weight for SST run 1 correct go 

name  \
0                  collection_id   
1                mrisstr1bw01_id   
2                     dataset_id   
3                     subjectkey   
4                 src_subject_id   
5                 interview_date   
6                  interview_age   
7                         gender   
8                      eventname   
9       tfmri_sstr1_beta_visitid   
10           tfmri_sstr1_beta_tr   
11       tfmri_sstr1_beta_numtrs   
12          tfmri_sstr1_beta_dof   
13        tfmri_sstr1_beta_nvols   
14     tfmri_sstr1_beta_sthnvols   
15   tfmri_sstr1_beta_meanmotion   
16    tfmri_sstr1_beta_maxmotion   
17    tfmri_sstr1_beta_meantrans   
18     tfmri_sstr1_beta_maxtrans   
19      tfmri_sstr1_beta_meanrot   
20       tfmri_sstr1_beta_maxrot   
21                 tfmri_sstr1_1   
22                 tfmri_sstr1_2   
23                 tfmri_sstr1_3   
24                 tfmri_sstr1_4   
25                 tfmri_sstr1_5   
26                 tfmri_sstr1_6   
27                 tfmri_sstr1_7   
28                 tfmri_sstr1_8   
29                 tfmri_sstr1_9   
30                tfmri_sstr1_10   
31                tfmri_sstr1_11   
32                tfmri_sstr1_12   
33                tfmri_sstr1_13   
34                tfmri_sstr1_14   
35                tfmri_sstr1_15   
36                tfmri_sstr1_16   
37                tfmri_sstr1_17   
38                tfmri_sstr1_18   
39                tfmri_sstr1_19   
40                tfmri_sstr1_20   
41                tfmri_sstr1_21   
42                tfmri_sstr1_22   
43                tfmri_sstr1_23   
44                tfmri_sstr1_24   
45                tfmri_sstr1_25   
46                tfmri_sstr1_26   
47                tfmri_sstr1_27   
48                tfmri_sstr1_28   
49                tfmri_sstr1_29   
50                tfmri_sstr1_30   
51                tfmri_sstr1_31   
52                tfmri_sstr1_32   
53                tfmri_sstr1_33   
54                tfmri_sstr1_34   
55                tfmri_sstr1_35   
56                tfmri_sstr1_36   
57                tfmri_sstr1_37   
58                tfmri_sstr1_38   
59                tfmri_sstr1_39   
60                tfmri_sstr1_40   
61                tfmri_sstr1_41   
62                tfmri_sstr1_42   
63                tfmri_sstr1_43   
64                tfmri_sstr1_44   
65                tfmri_sstr1_45   
66                tfmri_sstr1_46   
67                tfmri_sstr1_47   
68                tfmri_sstr1_48   
69                tfmri_sstr1_49   
70                tfmri_sstr1_50   
71                tfmri_sstr1_51   
72                tfmri_sstr1_52   
73                tfmri_sstr1_53   
74                tfmri_sstr1_54   
75                tfmri_sstr1_55   
76                tfmri_sstr1_56   
77                tfmri_sstr1_57   
78                tfmri_sstr1_58   
79                tfmri_sstr1_59   
80                tfmri_sstr1_60   
81                tfmri_sstr1_61   
82                tfmri_sstr1_62   
83                tfmri_sstr1_63   
84                tfmri_sstr1_64   
85                tfmri_sstr1_65   
86                tfmri_sstr1_66   
87                tfmri_sstr1_67   
88                tfmri_sstr1_68   
89                tfmri_sstr1_69   
90                tfmri_sstr1_70   
91                tfmri_sstr1_71   
92                tfmri_sstr1_72   
93                tfmri_sstr1_73   
94                tfmri_sstr1_74   
95                tfmri_sstr1_75   
96                tfmri_sstr1_76   
97                tfmri_sstr1_77   
98                tfmri_sstr1_78   
99                tfmri_sstr1_79   
100               tfmri_sstr1_80   
101               tfmri_sstr1_81   
102               tfmri_sstr1_82   
103               tfmri_sstr1_83   
104               tfmri_sstr1_84   
105               tfmri_sstr1_85   
106               tfmri_sstr1_86   
107               tfmri_sstr1_87   
108               tfmri_sstr1_88   
109               tfmri_sstr1_89   
110               tfmri_sstr1_90

In [56]:
fn = 'mrisstr2bw01'
mid_t, mid_l = load_abcd_table(abcd_table_path + f'{fn}.txt')
pd.unique(mid_l.doc.str.split('in APARC').str[0].str.split('in ASEG').str[0])
mid_l

array(['collection_id', 'mrisstr2bw01_id', 'dataset_id',
       'The NDAR Global Unique Identifier (GUID) for research subject',
       "Subject ID how it's defined in lab/project",
       'Date on which the interview/genetic test/sampling/imaging/biospecimen was completed. MM/DD/YYYY',
       'Age in months at the time of the interview/test/sampling/imaging.',
       'Sex of the subject',
       'The event name for which the data was collected', 'Visit name',
       'Pulse repetition time in seconds',
       'Number of frames in acquisition', 'Degrees of freedom',
       'Number of frames after removing dummy frames',
       'Number of frames with FD < 0.2',
       'Average framewise displacement in mm',
       'Maximum framewise displacement in mm',
       'Average framewise translation in mm',
       'Maximum framewise translation in mm',
       'Average framewise rotation in radians',
       'Maximum framewise rotation in radians',
       'Mean beta weight for SST run 2 correct go 

name  \
0                  collection_id   
1                mrisstr2bw01_id   
2                     dataset_id   
3                     subjectkey   
4                 src_subject_id   
5                 interview_date   
6                  interview_age   
7                         gender   
8                      eventname   
9       tfmri_sstr2_beta_visitid   
10           tfmri_sstr2_beta_tr   
11       tfmri_sstr2_beta_numtrs   
12          tfmri_sstr2_beta_dof   
13        tfmri_sstr2_beta_nvols   
14     tfmri_sstr2_beta_sthnvols   
15   tfmri_sstr2_beta_meanmotion   
16    tfmri_sstr2_beta_maxmotion   
17    tfmri_sstr2_beta_meantrans   
18     tfmri_sstr2_beta_maxtrans   
19      tfmri_sstr2_beta_meanrot   
20       tfmri_sstr2_beta_maxrot   
21                 tfmri_sstr2_1   
22                 tfmri_sstr2_2   
23                 tfmri_sstr2_3   
24                 tfmri_sstr2_4   
25                 tfmri_sstr2_5   
26                 tfmri_sstr2_6   
27                 tfmri_sstr2_7   
28                 tfmri_sstr2_8   
29                 tfmri_sstr2_9   
30                tfmri_sstr2_10   
31                tfmri_sstr2_11   
32                tfmri_sstr2_12   
33                tfmri_sstr2_13   
34                tfmri_sstr2_14   
35                tfmri_sstr2_15   
36                tfmri_sstr2_16   
37                tfmri_sstr2_17   
38                tfmri_sstr2_18   
39                tfmri_sstr2_19   
40                tfmri_sstr2_20   
41                tfmri_sstr2_21   
42                tfmri_sstr2_22   
43                tfmri_sstr2_23   
44                tfmri_sstr2_24   
45                tfmri_sstr2_25   
46                tfmri_sstr2_26   
47                tfmri_sstr2_27   
48                tfmri_sstr2_28   
49                tfmri_sstr2_29   
50                tfmri_sstr2_30   
51                tfmri_sstr2_31   
52                tfmri_sstr2_32   
53                tfmri_sstr2_33   
54                tfmri_sstr2_34   
55                tfmri_sstr2_35   
56                tfmri_sstr2_36   
57                tfmri_sstr2_37   
58                tfmri_sstr2_38   
59                tfmri_sstr2_39   
60                tfmri_sstr2_40   
61                tfmri_sstr2_41   
62                tfmri_sstr2_42   
63                tfmri_sstr2_43   
64                tfmri_sstr2_44   
65                tfmri_sstr2_45   
66                tfmri_sstr2_46   
67                tfmri_sstr2_47   
68                tfmri_sstr2_48   
69                tfmri_sstr2_49   
70                tfmri_sstr2_50   
71                tfmri_sstr2_51   
72                tfmri_sstr2_52   
73                tfmri_sstr2_53   
74                tfmri_sstr2_54   
75                tfmri_sstr2_55   
76                tfmri_sstr2_56   
77                tfmri_sstr2_57   
78                tfmri_sstr2_58   
79                tfmri_sstr2_59   
80                tfmri_sstr2_60   
81                tfmri_sstr2_61   
82                tfmri_sstr2_62   
83                tfmri_sstr2_63   
84                tfmri_sstr2_64   
85                tfmri_sstr2_65   
86                tfmri_sstr2_66   
87                tfmri_sstr2_67   
88                tfmri_sstr2_68   
89                tfmri_sstr2_69   
90                tfmri_sstr2_70   
91                tfmri_sstr2_71   
92                tfmri_sstr2_72   
93                tfmri_sstr2_73   
94                tfmri_sstr2_74   
95                tfmri_sstr2_75   
96                tfmri_sstr2_76   
97                tfmri_sstr2_77   
98                tfmri_sstr2_78   
99                tfmri_sstr2_79   
100               tfmri_sstr2_80   
101               tfmri_sstr2_81   
102               tfmri_sstr2_82   
103               tfmri_sstr2_83   
104               tfmri_sstr2_84   
105               tfmri_sstr2_85   
106               tfmri_sstr2_86   
107               tfmri_sstr2_87   
108               tfmri_sstr2_88   
109               tfmri_sstr2_89   
110               tfmri_sstr2_90

In [57]:
fn = 'nbackr101'
mid_t, mid_l = load_abcd_table(abcd_table_path + f'{fn}.txt')
pd.unique(mid_l.doc.str.split('in APARC').str[0].str.split('in ASEG').str[0])
mid_l

array(['collection_id', 'nbackr101_id', 'dataset_id',
       'The NDAR Global Unique Identifier (GUID) for research subject',
       "Subject ID how it's defined in lab/project",
       'Date on which the interview/genetic test/sampling/imaging/biospecimen was completed. MM/DD/YYYY',
       'Age in months at the time of the interview/test/sampling/imaging.',
       'Sex of the subject',
       'The event name for which the data was collected', 'Visit name',
       'Pulse repetition time in seconds',
       'Number of frames in acquisition', 'Degrees of freedom',
       'Number of frames after removing dummy frames',
       'Number of frames with FD < 0.2',
       'Average framewise displacement in mm',
       'Maximum framewise displacement in mm',
       'Average framewise translation in mm',
       'Maximum framewise translation in mm',
       'Average framewise rotation in radians',
       'Maximum framewise rotation in radians',
       'Mean beta weight for nBack run 1 0 back condi

name  \
0                     collection_id   
1                      nbackr101_id   
2                        dataset_id   
3                        subjectkey   
4                    src_subject_id   
5                    interview_date   
6                     interview_age   
7                            gender   
8                         eventname   
9     tfmri_nback_run1_beta_visitid   
10         tfmri_nback_run1_beta_tr   
11     tfmri_nback_run1_beta_numtrs   
12        tfmri_nback_run1_beta_dof   
13      tfmri_nback_run1_beta_nvols   
14   tfmri_nback_run1_beta_sthnvols   
15         tfmri_nback_run1_beta_mm   
16      tfmri_nback_run1b_maxmotion   
17      tfmri_nback_run1b_meantrans   
18   tfmri_nback_run1_beta_maxtrans   
19    tfmri_nback_run1_beta_meanrot   
20     tfmri_nback_run1_beta_maxrot   
21                 tfmri_nback_r1_1   
22                 tfmri_nback_r1_2   
23                 tfmri_nback_r1_3   
24                 tfmri_nback_r1_4   
25                 tfmri_nback_r1_5   
26                 tfmri_nback_r1_6   
27                 tfmri_nback_r1_7   
28                 tfmri_nback_r1_8   
29                 tfmri_nback_r1_9   
30                tfmri_nback_r1_10   
31                tfmri_nback_r1_11   
32                tfmri_nback_r1_12   
33                tfmri_nback_r1_13   
34                tfmri_nback_r1_14   
35                tfmri_nback_r1_15   
36                tfmri_nback_r1_16   
37                tfmri_nback_r1_17   
38                tfmri_nback_r1_18   
39                tfmri_nback_r1_19   
40                tfmri_nback_r1_20   
41                tfmri_nback_r1_21   
42                tfmri_nback_r1_22   
43                tfmri_nback_r1_23   
44                tfmri_nback_r1_24   
45                tfmri_nback_r1_25   
46                tfmri_nback_r1_26   
47                tfmri_nback_r1_27   
48                tfmri_nback_r1_28   
49                tfmri_nback_r1_29   
50                tfmri_nback_r1_30   
51                tfmri_nback_r1_31   
52                tfmri_nback_r1_32   
53                tfmri_nback_r1_33   
54                tfmri_nback_r1_34   
55                tfmri_nback_r1_35   
56                tfmri_nback_r1_36   
57                tfmri_nback_r1_37   
58                tfmri_nback_r1_38   
59                tfmri_nback_r1_39   
60                tfmri_nback_r1_40   
61                tfmri_nback_r1_41   
62                tfmri_nback_r1_42   
63                tfmri_nback_r1_43   
64                tfmri_nback_r1_44   
65                tfmri_nback_r1_45   
66                tfmri_nback_r1_46   
67                tfmri_nback_r1_47   
68                tfmri_nback_r1_48   
69                tfmri_nback_r1_49   
70                tfmri_nback_r1_50   
71                tfmri_nback_r1_51   
72                tfmri_nback_r1_52   
73                tfmri_nback_r1_53   
74                tfmri_nback_r1_54   
75                tfmri_nback_r1_55   
76                tfmri_nback_r1_56   
77                tfmri_nback_r1_57   
78                tfmri_nback_r1_58   
79                tfmri_nback_r1_59   
80                tfmri_nback_r1_60   
81                tfmri_nback_r1_61   
82                tfmri_nback_r1_62   
83                tfmri_nback_r1_63   
84                tfmri_nback_r1_64   
85                tfmri_nback_r1_65   
86                tfmri_nback_r1_66   
87                tfmri_nback_r1_67   
88                tfmri_nback_r1_68   
89                tfmri_nback_r1_69   
90                tfmri_nback_r1_70   
91                tfmri_nback_r1_71   
92                tfmri_nback_r1_72   
93                tfmri_nback_r1_73   
94                tfmri_nback_r1_74   
95                tfmri_nback_r1_75   
96                tfmri_nback_r1_76   
97                tfmri_nback_r1_77   
98                tfmri_nback_r1_78   
99                tfmri_nback_r1_79   
100               tfmri_nback_r1_80   
101               tfmri_nback_r1_81   
102           

In [63]:
fn = 'abcd_smrip101'
mid_t, mid_l = load_abcd_table(abcd_table_path + f'{fn}.txt')
pd.unique(mid_l.doc.str.split('of APARC').str[0].str.split('of ASEG').str[0])

mid_l

array(['collection_id', 'abcd_smrip101_id', 'dataset_id',
       'The NDAR Global Unique Identifier (GUID) for research subject',
       "Subject ID how it's defined in lab/project",
       'Date on which the interview/genetic test/sampling/imaging/biospecimen was completed. MM/DD/YYYY',
       'Age in months at the time of the interview/test/sampling/imaging.',
       'Sex of the subject',
       'The event name for which the data was collected', 'Visit name',
       'Cortical thickness in mm ',
       'Weighted average thickness for genetically derived parcellation with 2 clusters-lh-frontal',
       'Weighted average thickness for genetically derived parcellation with 2 clusters-lh-posterior',
       'Weighted average thickness for genetically derived parcellation with 4 clusters-lh-frontal',
       'Weighted average thickness for genetically derived parcellation with 4 clusters-lh-occipital',
       'Weighted average thickness for genetically derived parcellation with 4 clusters-lh

name  \
0                     collection_id   
1                  abcd_smrip101_id   
2                        dataset_id   
3                        subjectkey   
4                    src_subject_id   
5                    interview_date   
6                     interview_age   
7                            gender   
8                         eventname   
9                      smri_visitid   
10        smri_thick_cdk_banksstslh   
11         smri_thick_cdk_cdacatelh   
12          smri_thick_cdk_cdmdfrlh   
13          smri_thick_cdk_cuneuslh   
14          smri_thick_cdk_ehinallh   
15        smri_thick_cdk_fusiformlh   
16            smri_thick_cdk_ifpllh   
17            smri_thick_cdk_iftmlh   
18          smri_thick_cdk_ihcatelh   
19            smri_thick_cdk_locclh   
20           smri_thick_cdk_lobfrlh   
21         smri_thick_cdk_linguallh   
22           smri_thick_cdk_mobfrlh   
23            smri_thick_cdk_mdtmlh   
24        smri_thick_cdk_parahpallh   
25          smri_thick_cdk_paracnlh   
26         smri_thick_cdk_parsopclh   
27        smri_thick_cdk_parsobislh   
28       smri_thick_cdk_parstgrislh   
29          smri_thick_cdk_pericclh   
30          smri_thick_cdk_postcnlh   
31          smri_thick_cdk_ptcatelh   
32           smri_thick_cdk_precnlh   
33              smri_thick_cdk_pclh   
34         smri_thick_cdk_rracatelh   
35          smri_thick_cdk_rrmdfrlh   
36            smri_thick_cdk_sufrlh   
37            smri_thick_cdk_supllh   
38            smri_thick_cdk_sutmlh   
39              smri_thick_cdk_smlh   
40          smri_thick_cdk_frpolelh   
41          smri_thick_cdk_tmpolelh   
42           smri_thick_cdk_trvtmlh   
43          smri_thick_cdk_insulalh   
44        smri_thick_cdk_banksstsrh   
45         smri_thick_cdk_cdacaterh   
46          smri_thick_cdk_cdmdfrrh   
47          smri_thick_cdk_cuneusrh   
48          smri_thick_cdk_ehinalrh   
49        smri_thick_cdk_fusiformrh   
50            smri_thick_cdk_ifplrh   
51            smri_thick_cdk_iftmrh   
52          smri_thick_cdk_ihcaterh   
53            smri_thick_cdk_loccrh   
54           smri_thick_cdk_lobfrrh   
55         smri_thick_cdk_lingualrh   
56           smri_thick_cdk_mobfrrh   
57            smri_thick_cdk_mdtmrh   
58        smri_thick_cdk_parahpalrh   
59          smri_thick_cdk_paracnrh   
60         smri_thick_cdk_parsopcrh   
61        smri_thick_cdk_parsobisrh   
62       smri_thick_cdk_parstgrisrh   
63          smri_thick_cdk_periccrh   
64          smri_thick_cdk_postcnrh   
65          smri_thick_cdk_ptcaterh   
66           smri_thick_cdk_precnrh   
67              smri_thick_cdk_pcrh   
68         smri_thick_cdk_rracaterh   
69          smri_thick_cdk_rrmdfrrh   
70            smri_thick_cdk_sufrrh   
71            smri_thick_cdk_suplrh   
72            smri_thick_cdk_sutmrh   
73              smri_thick_cdk_smrh   
74          smri_thick_cdk_frpolerh   
75          smri_thick_cdk_tmpolerh   
76           smri_thick_cdk_trvtmrh   
77          smri_thick_cdk_insularh   
78              smri_thick_cf2_frlh   
79              smri_thick_cf2_ptlh   
80              smri_thick_cf4_frlh   
81             smri_thick_cf4_occlh   
82              smri_thick_cf4_tmlh   
83              smri_thick_cf4_pllh   
84             smri_thick_cf12_cnlh   
85            smri_thick_cf12_occlh   
86         smri_thick_cf12_ptoltmlh   
87           smri_thick_cf12_supllh   
88           smri_thick_cf12_obfrlh   
89           smri_thick_cf12_sutmlh   
90           smri_thick_cf12_ifpllh   
91           smri_thick_cf12_dmfrlh   
92          smri_thick_cf12_aomtmlh   
93             smri_thick_cf12_pclh   
94        smri_thick_cf12_dlprefrlh   
95        smri_thick_cf12_parsopclh   
96              smri_thick_cf2_frrh   
97              smri_thick_cf2_ptrh   
98              smri_thick_cf4_frrh   
99             smri_thick_cf4_occrh   
100             smri_thick_cf4_tmrh   
101             smri_thick_cf4_plrh   
102           

In [62]:
fn = 'abcd_smrip201'
mid_t, mid_l = load_abcd_table(abcd_table_path + f'{fn}.txt')
mid_l

name  \
0                  collection_id   
1               abcd_smrip201_id   
2                     dataset_id   
3                     subjectkey   
4                 src_subject_id   
5                 interview_date   
6                  interview_age   
7                         gender   
8     smri_t2ww02_cdk_banksstslh   
9    smri_t2ww02_cdk_cdatcgatelh   
10       smri_t2ww02_cdk_cdmdflh   
11      smri_t2ww02_cdk_cuneuslh   
12      smri_t2ww02_cdk_ehinallh   
13    smri_t2ww02_cdk_fusiformlh   
14        smri_t2ww02_cdk_ifpllh   
15        smri_t2ww02_cdk_iftmlh   
16     smri_t2ww02_cdk_ihcgatelh   
17       smri_t2ww02_cdk_ltocclh   
18      smri_t2ww02_cdk_ltoboflh   
19     smri_t2ww02_cdk_linguallh   
20       smri_t2ww02_cdk_moboflh   
21        smri_t2ww02_cdk_mdtmlh   
22    smri_t2ww02_cdk_parahpallh   
23      smri_t2ww02_cdk_paractlh   
24        smri_t2ww02_cdk_popclh   
25     smri_t2ww02_cdk_pobalislh   
26     smri_t2ww02_cdk_parstgslh   
27      smri_t2ww02_cdk_pericclh   
28      smri_t2ww02_cdk_postctlh   
29     smri_t2ww02_cdk_pscgatelh   
30       smri_t2ww02_cdk_prectlh   
31          smri_t2ww02_cdk_pnlh   
32   smri_t2ww02_cdk_rtatcgatelh   
33       smri_t2ww02_cdk_rtmdflh   
34         smri_t2ww02_cdk_suflh   
35        smri_t2ww02_cdk_supllh   
36        smri_t2ww02_cdk_sutmlh   
37          smri_t2ww02_cdk_smlh   
38       smri_t2ww02_cdk_fpolelh   
39      smri_t2ww02_cdk_tmpolelh   
40        smri_t2ww02_cdk_tvtmlh   
41      smri_t2ww02_cdk_insulalh   
42    smri_t2ww02_cdk_banksstsrh   
43   smri_t2ww02_cdk_cdatcgaterh   
44       smri_t2ww02_cdk_cdmdfrh   
45      smri_t2ww02_cdk_cuneusrh   
46      smri_t2ww02_cdk_ehinalrh   
47    smri_t2ww02_cdk_fusiformrh   
48        smri_t2ww02_cdk_ifplrh   
49        smri_t2ww02_cdk_iftmrh   
50     smri_t2ww02_cdk_ihcgaterh   
51       smri_t2ww02_cdk_ltoccrh   
52      smri_t2ww02_cdk_ltobofrh   
53     smri_t2ww02_cdk_lingualrh   
54       smri_t2ww02_cdk_mobofrh   
55        smri_t2ww02_cdk_mdtmrh   
56    smri_t2ww02_cdk_parahpalrh   
57      smri_t2ww02_cdk_paractrh   
58        smri_t2ww02_cdk_popcrh   
59     smri_t2ww02_cdk_pobalisrh   
60     smri_t2ww02_cdk_parstgsrh   
61      smri_t2ww02_cdk_periccrh   
62      smri_t2ww02_cdk_postctrh   
63     smri_t2ww02_cdk_pscgaterh   
64       smri_t2ww02_cdk_prectrh   
65          smri_t2ww02_cdk_pnrh   
66   smri_t2ww02_cdk_rtatcgaterh   
67       smri_t2ww02_cdk_rtmdfrh   
68         smri_t2ww02_cdk_sufrh   
69        smri_t2ww02_cdk_suplrh   
70        smri_t2ww02_cdk_sutmrh   
71          smri_t2ww02_cdk_smrh   
72       smri_t2ww02_cdk_fpolerh   
73      smri_t2ww02_cdk_tmpolerh   
74        smri_t2ww02_cdk_tvtmrh   
75      smri_t2ww02_cdk_insularh   
76           smri_t2ww02_cf2_flh   
77          smri_t2ww02_cf2_pslh   
78           smri_t2ww02_cf4_flh   
79         smri_t2ww02_cf4_occlh   
80          smri_t2ww02_cf4_tmlh   
81          smri_t2ww02_cf4_pllh   
82         smri_t2ww02_cf12_ctlh   
83        smri_t2ww02_cf12_occlh   
84     smri_t2ww02_cf12_polttmlh   
85       smri_t2ww02_cf12_supllh   
86       smri_t2ww02_cf12_oboflh   
87       smri_t2ww02_cf12_sutmlh   
88       smri_t2ww02_cf12_ifpllh   
89        smri_t2ww02_cf12_dmflh   
90      smri_t2ww02_cf12_aomtmlh   
91         smri_t2ww02_cf12_pnlh   
92    smri_t2ww02_cf12_dltpreflh   
93       smri_t2ww02_cf12_popclh   
94           smri_t2ww02_cf2_frh   
95          smri_t2ww02_cf2_psrh   
96           smri_t2ww02_cf4_frh   
97         smri_t2ww02_cf4_occrh   
98          smri_t2ww02_cf4_tmrh   
99          smri_t2ww02_cf4_plrh   
100        smri_t2ww02_cf12_ctrh   
101       smri_t2ww02_cf12_occrh   
102    smri_t2ww02_cf12_polttmrh   
103      smri_t2ww02_cf12_suplrh   
104      smri_t2ww02_cf12_obofrh   
105      smri_t2ww02_cf12_sutmrh   
106      smri_t2ww02_cf12_ifplrh   
107       smri_t2ww02_cf12_dmfrh   
108     smri_t2ww02_cf12_aomtmrh   
109        smri_t2ww02_cf12_pnrh   
110   smri_t2ww02_cf12_dltprefrh

In [64]:
fn = 'abcd_dti_p101'
mid_t, mid_l = load_abcd_table(abcd_table_path + f'{fn}.txt')
mid_l

name  \
0                    collection_id   
1                 abcd_dti_p101_id   
2                       dataset_id   
3                       subjectkey   
4                   src_subject_id   
5                   interview_date   
6                    interview_age   
7                           gender   
8                        eventname   
9                 dmri_dti_visitid   
10             dmri_dti_meanmotion   
11              dmri_dti_meantrans   
12                dmri_dti_meanrot   
13         dmri_dtifa_fiberat_fxrh   
14         dmri_dtifa_fiberat_fxlh   
15        dmri_dtifa_fiberat_cgcrh   
16        dmri_dtifa_fiberat_cgclh   
17        dmri_dtifa_fiberat_cghrh   
18        dmri_dtifa_fiberat_cghlh   
19        dmri_dtifa_fiberat_cstrh   
20        dmri_dtifa_fiberat_cstlh   
21        dmri_dtifa_fiberat_atrrh   
22        dmri_dtifa_fiberat_atrlh   
23        dmri_dtifa_fiberat_uncrh   
24        dmri_dtifa_fiberat_unclh   
25        dmri_dtifa_fiberat_ilfrh   
26        dmri_dtifa_fiberat_ilflh   
27        dmri_dtifa_fiberat_iforh   
28        dmri_dtifa_fiberat_ifolh   
29         dmri_dtifa_fiberat_fmaj   
30         dmri_dtifa_fiberat_fmin   
31           dmri_dtifa_fiberat_cc   
32        dmri_dtifa_fiberat_slfrh   
33        dmri_dtifa_fiberat_slflh   
34       dmri_dtifa_fiberat_tslfrh   
35       dmri_dtifa_fiberat_tslflh   
36       dmri_dtifa_fiberat_pslfrh   
37       dmri_dtifa_fiberat_pslflh   
38        dmri_dtifa_fiberat_scsrh   
39        dmri_dtifa_fiberat_scslh   
40       dmri_dtifa_fiberat_fscsrh   
41       dmri_dtifa_fiberat_fscslh   
42       dmri_dtifa_fiberat_pscsrh   
43       dmri_dtifa_fiberat_pscslh   
44       dmri_dtifa_fiberat_sifcrh   
45       dmri_dtifa_fiberat_sifclh   
46      dmri_dtifa_fiberat_ifsfcrh   
47      dmri_dtifa_fiberat_ifsfclh   
48      dmri_dtifa_fiberat_fxcutrh   
49      dmri_dtifa_fiberat_fxcutlh   
50    dmri_dtifa_fiberat_allfibers   
51     dmri_dtifa_fiberat_allfccrh   
52     dmri_dtifa_fiberat_allfcclh   
53     dmri_dtifa_fiberat_allfibrh   
54     dmri_dtifa_fiberat_allfiblh   
55         dmri_dtimd_fiberat_fxrh   
56         dmri_dtimd_fiberat_fxlh   
57        dmri_dtimd_fiberat_cgcrh   
58        dmri_dtimd_fiberat_cgclh   
59        dmri_dtimd_fiberat_cghrh   
60        dmri_dtimd_fiberat_cghlh   
61        dmri_dtimd_fiberat_cstrh   
62        dmri_dtimd_fiberat_cstlh   
63        dmri_dtimd_fiberat_atrrh   
64        dmri_dtimd_fiberat_atrlh   
65        dmri_dtimd_fiberat_uncrh   
66        dmri_dtimd_fiberat_unclh   
67        dmri_dtimd_fiberat_ilfrh   
68        dmri_dtimd_fiberat_ilflh   
69        dmri_dtimd_fiberat_iforh   
70        dmri_dtimd_fiberat_ifolh   
71         dmri_dtimd_fiberat_fmaj   
72         dmri_dtimd_fiberat_fmin   
73           dmri_dtimd_fiberat_cc   
74        dmri_dtimd_fiberat_slfrh   
75        dmri_dtimd_fiberat_slflh   
76       dmri_dtimd_fiberat_tslfrh   
77       dmri_dtimd_fiberat_tslflh   
78       dmri_dtimd_fiberat_pslfrh   
79       dmri_dtimd_fiberat_pslflh   
80        dmri_dtimd_fiberat_scsrh   
81        dmri_dtimd_fiberat_scslh   
82       dmri_dtimd_fiberat_fscsrh   
83       dmri_dtimd_fiberat_fscslh   
84       dmri_dtimd_fiberat_pscsrh   
85       dmri_dtimd_fiberat_pscslh   
86       dmri_dtimd_fiberat_sifcrh   
87       dmri_dtimd_fiberat_sifclh   
88      dmri_dtimd_fiberat_ifsfcrh   
89      dmri_dtimd_fiberat_ifsfclh   
90      dmri_dtimd_fiberat_fxcutrh   
91      dmri_dtimd_fiberat_fxcutlh   
92    dmri_dtimd_fiberat_allfibers   
93     dmri_dtimd_fiberat_allfccrh   
94     dmri_dtimd_fiberat_allfcclh   
95     dmri_dtimd_fiberat_allfibrh   
96     dmri_dtimd_fiberat_allfiblh   
97         dmri_dtild_fiberat_fxrh   
98         dmri_dtild_fiberat_fxlh   
99        dmri_dtild_fiberat_cgcrh   
100       dmri_dtild_fiberat_cgclh   
101       dmri_dtild_fiberat_cghrh   
102       dmri_dtild_fiberat_cghlh   
103       dmri_dtild_fiberat_cstrh   
104       dmri_dtild_fiberat_cstlh   
10

In [65]:
fn = 'abcd_dti_p201'
mid_t, mid_l = load_abcd_table(abcd_table_path + f'{fn}.txt')
mid_l

name  \
0                     collection_id   
1                  abcd_dti_p201_id   
2                        dataset_id   
3                        subjectkey   
4                    src_subject_id   
5                    interview_date   
6                     interview_age   
7                            gender   
8            dmri_dtildgm_cdsn_bslh   
9       dmri_dtildgm_cdsn_cdacatelh   
10         dmri_dtildgm_cdsn_cdmflh   
11       dmri_dtildgm_cdsn_cuneuslh   
12       dmri_dtildgm_cdsn_ehinallh   
13           dmri_dtildgm_cdsn_fflh   
14         dmri_dtildgm_cdsn_ifpalh   
15         dmri_dtildgm_cdsn_iftmlh   
16       dmri_dtildgm_cdsn_ihcatelh   
17          dmri_dtildgm_cdsn_loclh   
18        dmri_dtildgm_cdsn_loboflh   
19            dmri_dtildgm_cdsn_llh   
20       dmri_dtildgm_cdsn_mdoboflh   
21          dmri_dtildgm_cdsn_mtmlh   
22        dmri_dtildgm_cdsn_phpallh   
23          dmri_dtildgm_cdsn_pcllh   
24         dmri_dtildgm_cdsn_pprslh   
25       dmri_dtildgm_cdsn_pbalislh   
26         dmri_dtildgm_cdsn_ptislh   
27      dmri_dtildgm_cdsn_periccelh   
28       dmri_dtildgm_cdsn_postcllh   
29       dmri_dtildgm_cdsn_pscatelh   
30        dmri_dtildgm_cdsn_precllh   
31           dmri_dtildgm_cdsn_pnlh   
32      dmri_dtildgm_cdsn_rlacatelh   
33         dmri_dtildgm_cdsn_rlmflh   
34          dmri_dtildgm_cdsn_srflh   
35         dmri_dtildgm_cdsn_srpalh   
36         dmri_dtildgm_cdsn_srtmlh   
37          dmri_dtildgm_cdsn_umllh   
38        dmri_dtildgm_cdsn_fpolelh   
39       dmri_dtildgm_cdsn_tmpolelh   
40        dmri_dtildgm_cdsn_trvtmlh   
41       dmri_dtildgm_cdsn_insulalh   
42           dmri_dtildgm_cdsn_bsrh   
43      dmri_dtildgm_cdsn_cdacaterh   
44         dmri_dtildgm_cdsn_cdmfrh   
45       dmri_dtildgm_cdsn_cuneusrh   
46       dmri_dtildgm_cdsn_ehinalrh   
47           dmri_dtildgm_cdsn_ffrh   
48         dmri_dtildgm_cdsn_ifparh   
49         dmri_dtildgm_cdsn_iftmrh   
50       dmri_dtildgm_cdsn_ihcaterh   
51          dmri_dtildgm_cdsn_locrh   
52        dmri_dtildgm_cdsn_lobofrh   
53            dmri_dtildgm_cdsn_lrh   
54       dmri_dtildgm_cdsn_mdobofrh   
55          dmri_dtildgm_cdsn_mtmrh   
56        dmri_dtildgm_cdsn_phpalrh   
57          dmri_dtildgm_cdsn_pclrh   
58         dmri_dtildgm_cdsn_pprsrh   
59       dmri_dtildgm_cdsn_pbalisrh   
60         dmri_dtildgm_cdsn_ptisrh   
61      dmri_dtildgm_cdsn_periccerh   
62       dmri_dtildgm_cdsn_postclrh   
63       dmri_dtildgm_cdsn_pscaterh   
64        dmri_dtildgm_cdsn_preclrh   
65           dmri_dtildgm_cdsn_pnrh   
66      dmri_dtildgm_cdsn_rlacaterh   
67         dmri_dtildgm_cdsn_rlmfrh   
68          dmri_dtildgm_cdsn_srfrh   
69         dmri_dtildgm_cdsn_srparh   
70         dmri_dtildgm_cdsn_srtmrh   
71          dmri_dtildgm_cdsn_umlrh   
72        dmri_dtildgm_cdsn_fpolerh   
73       dmri_dtildgm_cdsn_tmpolerh   
74        dmri_dtildgm_cdsn_trvtmrh   
75       dmri_dtildgm_cdsn_insularh   
76         dmri_dtildgm_cdsn_meanlh   
77         dmri_dtildgm_cdsn_meanrh   
78           dmri_dtildgm_cdsn_mean   
79           dmri_dtitdgm_cdsn_bslh   
80      dmri_dtitdgm_cdsn_cdacatelh   
81         dmri_dtitdgm_cdsn_cdmflh   
82       dmri_dtitdgm_cdsn_cuneuslh   
83       dmri_dtitdgm_cdsn_ehinallh   
84           dmri_dtitdgm_cdsn_fflh   
85         dmri_dtitdgm_cdsn_ifpalh   
86         dmri_dtitdgm_cdsn_iftmlh   
87       dmri_dtitdgm_cdsn_ihcatelh   
88          dmri_dtitdgm_cdsn_loclh   
89        dmri_dtitdgm_cdsn_loboflh   
90            dmri_dtitdgm_cdsn_llh   
91       dmri_dtitdgm_cdsn_mdoboflh   
92          dmri_dtitdgm_cdsn_mtmlh   
93        dmri_dtitdgm_cdsn_phpallh   
94          dmri_dtitdgm_cdsn_pcllh   
95         dmri_dtitdgm_cdsn_pprslh   
96       dmri_dtitdgm_cdsn_pbalislh   
97         dmri_dtitdgm_cdsn_ptislh   
98      dmri_dtitdgm_cdsn_periccelh   
99       dmri_dtitdgm_cdsn_postcllh   
100      dmri_dtitdgm_cdsn_pscatelh   
101       dmri_dtitdgm_cdsn_precllh   
102          d

In [84]:
fn = 'nbackr201'
mid_t, mid_l = load_abcd_table(abcd_table_path + f'{fn}.txt')
mid_l

name  \
0                    collection_id   
1                     nbackr201_id   
2                       dataset_id   
3                       subjectkey   
4                   src_subject_id   
5                   interview_date   
6                    interview_age   
7                           gender   
8                        eventname   
9      tfmri_nback_r2_beta_visitid   
10          tfmri_nback_r2_beta_tr   
11      tfmri_nback_r2_beta_numtrs   
12         tfmri_nback_r2_beta_dof   
13       tfmri_nback_r2_beta_nvols   
14    tfmri_nback_r2_beta_sthnvols   
15          tfmri_nback_r2_beta_mm   
16   tfmri_nback_r2_beta_maxmotion   
17   tfmri_nback_r2_beta_meantrans   
18    tfmri_nback_r2_beta_maxtrans   
19     tfmri_nback_r2_beta_meanrot   
20      tfmri_nback_r2_beta_maxrot   
21                tfmri_nback_r2_1   
22                tfmri_nback_r2_2   
23                tfmri_nback_r2_3   
24                tfmri_nback_r2_4   
25                tfmri_nback_r2_5   
26                tfmri_nback_r2_6   
27                tfmri_nback_r2_7   
28                tfmri_nback_r2_8   
29                tfmri_nback_r2_9   
30               tfmri_nback_r2_10   
31               tfmri_nback_r2_11   
32               tfmri_nback_r2_12   
33               tfmri_nback_r2_13   
34               tfmri_nback_r2_14   
35               tfmri_nback_r2_15   
36               tfmri_nback_r2_16   
37               tfmri_nback_r2_17   
38               tfmri_nback_r2_18   
39               tfmri_nback_r2_19   
40               tfmri_nback_r2_20   
41               tfmri_nback_r2_21   
42               tfmri_nback_r2_22   
43               tfmri_nback_r2_23   
44               tfmri_nback_r2_24   
45               tfmri_nback_r2_25   
46               tfmri_nback_r2_26   
47               tfmri_nback_r2_27   
48               tfmri_nback_r2_28   
49               tfmri_nback_r2_29   
50               tfmri_nback_r2_30   
51               tfmri_nback_r2_31   
52               tfmri_nback_r2_32   
53               tfmri_nback_r2_33   
54               tfmri_nback_r2_34   
55               tfmri_nback_r2_35   
56               tfmri_nback_r2_36   
57               tfmri_nback_r2_37   
58               tfmri_nback_r2_38   
59               tfmri_nback_r2_39   
60               tfmri_nback_r2_40   
61               tfmri_nback_r2_41   
62               tfmri_nback_r2_42   
63               tfmri_nback_r2_43   
64               tfmri_nback_r2_44   
65               tfmri_nback_r2_45   
66               tfmri_nback_r2_46   
67               tfmri_nback_r2_47   
68               tfmri_nback_r2_48   
69               tfmri_nback_r2_49   
70               tfmri_nback_r2_50   
71               tfmri_nback_r2_51   
72               tfmri_nback_r2_52   
73               tfmri_nback_r2_53   
74               tfmri_nback_r2_54   
75               tfmri_nback_r2_55   
76               tfmri_nback_r2_56   
77               tfmri_nback_r2_57   
78               tfmri_nback_r2_58   
79               tfmri_nback_r2_59   
80               tfmri_nback_r2_60   
81               tfmri_nback_r2_61   
82               tfmri_nback_r2_62   
83               tfmri_nback_r2_63   
84               tfmri_nback_r2_64   
85               tfmri_nback_r2_65   
86               tfmri_nback_r2_66   
87               tfmri_nback_r2_67   
88               tfmri_nback_r2_68   
89               tfmri_nback_r2_69   
90               tfmri_nback_r2_70   
91               tfmri_nback_r2_71   
92               tfmri_nback_r2_72   
93               tfmri_nback_r2_73   
94               tfmri_nback_r2_74   
95               tfmri_nback_r2_75   
96               tfmri_nback_r2_76   
97               tfmri_nback_r2_77   
98               tfmri_nback_r2_78   
99               tfmri_nback_r2_79   
100              tfmri_nback_r2_80   
101              tfmri_nback_r2_81   
102              tfmri_nback_r2_82   
103              tfmri_nback_r2_83   
104              tfmri_nback_r2_84   
10

In [73]:
!ls tables

abcd_ant01.txt	       abcd_psb01.txt	  freesqc01.txt
abcd_asrs01.txt        abcd_ptsd01.txt	  lmtp201.txt
abcd_betnet02.txt      abcd_ra01.txt	  macv01.txt
abcd_bisbas01.txt      abcd_rb01.txt	  medsy01.txt
abcd_cbcl01.txt        abcd_rhds01.txt	  midaparc02.txt
abcd_cbcls01.txt       abcd_saiq02.txt	  midaparcp202.txt
abcd_crpf01.txt        abcd_screen01.txt  midr2bwp101.txt
abcddemo01.txt	       abcd_sds01.txt	  midr2bwp201.txt
abcd_devhxss01.txt     abcd_smrip101.txt  mribrec02.txt
abcd_dti_p101.txt      abcd_smrip201.txt  mriqc02.txt
abcd_dti_p201.txt      abcd_spacss01.txt  mriqcp202.txt
abcd_ehis01.txt        abcd_sscep01.txt   mrirscor02.txt
abcd_fes01.txt	       abcd_sscey01.txt   mri_rsi_p102.txt
abcd_hers01.txt        abcd_sst02.txt	  mri_rsi_p202.txt
abcd_hsss01.txt        abcd_stq01.txt	  mrisst02.txt
abcd_ksad01.txt        abcd_suss01.txt	  mrisstr1bw01.txt
abcd_ksad501.txt       abcd_svs01.txt	  mrisstr1sem01.txt
abcd_lt01.txt	       abcd_tbi01.txt	  mrisstr2bw01.txt
abcd

In [ ]:
fn = 'mrisstr2bw01'
mid_t, mid_l = load_abcd_table(abcd_table_path + f'{fn}.txt')
pd.unique(mid_l.doc.str.split('in APARC').str[0].str.split('in ASEG').str[0])

In [41]:
ABCDFile = namedtuple('ABCDFile', ['path', 'task', 'run', 'field_prefix', 'contrasts'])

In [ ]:
def load_abcd_table(path):
    table = pd.read_csv(path, skiprows=[1], header=0, sep='\t')
    labels = pd.read_csv(path, nrows=1, header=0, sep='\t')
    labels = labels.T.reset_index().rename(columns={'index':'name', 0:'doc'})
    return table, labels

In [ ]:
fns = ['abcd_midr1bwp101', 'abcd_midr1bwp201', 'midr2bwp101', 'midr2bwp201']
runs = [1, 1, 2, 2]
fps = ['tfmri_mid_run1_beta']

ABCDFile(mid_paths[i])

In [16]:

mid_paths = [abcd_table_path + pp + '.txt' for pp in mid_paths]

mid_contrasts = ['MID anticipation of reward versus neutral',
       'MID anticipation of loss versus neutral',
       'MID reward positive versus negative feeback',
       'MID loss positive versus negative feedback',
       'MID anticipation of large reward versus neutral',
       'MID anticipation of small reward versus neutral',
       'MID anticipation of large versus small reward',
       'MID anticipation of large loss versus neutral',
       'MID anticipation of small loss versus neutral',
       'MID anticipation of small versus large loss',
       'MID anticipation of large versus small loss']

mid_b_melt, mid_l = load_task_melt_contrasts(mid_paths, mid_contrasts, 'mid')

KeyError: 'eventname'

In [17]:
mid_paths

['tables/abcd_midr1bwp101.txt',
 'tables/abcd_midr1bwp201.txt',
 'tables/midr2bwp101.txt',
 'tables/midr2bwp201.txt']

In [48]:
path = mid_paths[1]
table, label = load_abcd_table(mid_paths[0])
on = None

#if table is None:
#    return load_abcd_table(path)
if on is None:
    on = ['subjectkey', 'interview_date']
new_table, new_label = load_abcd_table(path)

In [36]:
# Find drop common columns that aren't in the set we're merging on
drop_cols = label.loc[label.doc.isin(new_label.doc) & ~label.name.isin(on),'name'].values
new_table.drop(drop_cols, axis=1, inplace=True)
new_label = new_label[~new_label.name.isin(drop_cols) & ~new_label.name.isin(on)]

# Get table shapes for error checking
ts = table.shape
nts = new_table.shape
ls = label.shape
nls = new_label.shape

# Merge the tables
table = table.merge(new_table, how='outer',on=on, indicator=True)

In [ ]:
strip_prefix = 'tfmri_mid_run1_'

In [40]:
table.columns.str.replace(strip_prefix)

In [47]:
prefix_candidate_1 = table.columns[table.columns.str.contains('visitid')][0].replace('visitid','')
prefix_candidate_1 = table.columns[table.columns.str.contains('visitid')][0].replace('visitid','')

'tfmri_mid_run1_beta_'

In [33]:
# Check for success
assert table.shape[0] == ts[0] == nts[0]
assert table.shape[1] == (ts[1] + nts[1] - len(on))

# Merge labels
label = pd.concat([label, new_label]).reset_index(drop=True)

assert label.shape[0] == table.shape[1]
    

In [50]:
label

name  \
0                     collection_id   
1               abcd_midr1bwp101_id   
2                        dataset_id   
3                        subjectkey   
4                    src_subject_id   
5                    interview_date   
6                     interview_age   
7                            gender   
8                         eventname   
9       tfmri_mid_run1_beta_visitid   
10           tfmri_mid_run1_beta_tr   
11       tfmri_mid_run1_beta_numtrs   
12          tfmri_mid_run1_beta_dof   
13        tfmri_mid_run1_beta_nvols   
14           tfmri_mr1_beta_stnvols   
15                tfmri_mr1_beta_mm   
16         tfmri_mr1_beta_maxmotion   
17         tfmri_mr1_beta_meantrans   
18     tfmri_mid_run1_beta_maxtrans   
19      tfmri_mid_run1_beta_meanrot   
20       tfmri_mid_run1_beta_maxrot   
21       tfmri_mr1_arvn_bscs_cbwmlh   
22        tfmri_mr1_arvn_bscs_lvelh   
23       tfmri_mr1_arvn_bscs_iftvlh   
24      tfmri_mr1_arvn_bscs_crbwmlh   
25      tfmri_mr1_arvn_bscs_crbcxlh   
26         tfmri_mr1_arvn_bscs_tplh   
27        tfmri_mr1_arvn_bscs_ctelh   
28         tfmri_mr1_arvn_bscs_pulh   
29         tfmri_mr1_arvn_bscs_pdlh   
30     tfmri_mr1_arvn_bscs_3rdvicle   
31     tfmri_mr1_arvn_bscs_4thvicle   
32           tfmri_mr1_arvn_bscs_bs   
33       tfmri_mr1_arvn_bscs_hpuslh   
34         tfmri_mr1_arvn_bscs_aylh   
35          tfmri_mr1_arvn_bscs_csf   
36         tfmri_mr1_arvn_bscs_aalh   
37       tfmri_mr1_arvn_bscs_vtdclh   
38       tfmri_mr1_arvn_bscs_cbwmrh   
39        tfmri_mr1_arvn_bscs_lverh   
40        tfmri_mr1_arvn_bscs_iftvh   
41      tfmri_mr1_arvn_bscs_crbwmrh   
42      tfmri_mr1_arvn_bscs_crbcxrh   
43         tfmri_mr1_arvn_bscs_tprh   
44        tfmri_mr1_arvn_bscs_cterh   
45         tfmri_mr1_arvn_bscs_purh   
46         tfmri_mr1_arvn_bscs_pdrh   
47       tfmri_mr1_arvn_bscs_hpusrh   
48         tfmri_mr1_arvn_bscs_ayrh   
49         tfmri_mr1_arvn_bscs_aarh   
50       tfmri_mr1_arvn_bscs_vtdcrh   
51       tfmri_mr1_alvn_bscs_cbwmlh   
52        tfmri_mr1_alvn_bscs_lvelh   
53       tfmri_mr1_alvn_bscs_iftvlh   
54      tfmri_mr1_alvn_bscs_crbwmlh   
55      tfmri_mr1_alvn_bscs_crbcxlh   
56         tfmri_mr1_alvn_bscs_tplh   
57        tfmri_mr1_alvn_bscs_ctelh   
58         tfmri_mr1_alvn_bscs_pulh   
59         tfmri_mr1_alvn_bscs_pdlh   
60     tfmri_mr1_alvn_bscs_3rdvicle   
61     tfmri_mr1_alvn_bscs_4thvicle   
62           tfmri_mr1_alvn_bscs_bs   
63       tfmri_mr1_alvn_bscs_hpuslh   
64         tfmri_mr1_alvn_bscs_aylh   
65          tfmri_mr1_alvn_bscs_csf   
66         tfmri_mr1_alvn_bscs_aalh   
67       tfmri_mr1_alvn_bscs_vtdclh   
68       tfmri_mr1_alvn_bscs_cbwmrh   
69        tfmri_mr1_alvn_bscs_lverh   
70        tfmri_mr1_alvn_bscs_iftvh   
71      tfmri_mr1_alvn_bscs_crbwmrh   
72      tfmri_mr1_alvn_bscs_crbcxrh   
73         tfmri_mr1_alvn_bscs_tprh   
74        tfmri_mr1_alvn_bscs_cterh   
75         tfmri_mr1_alvn_bscs_purh   
76         tfmri_mr1_alvn_bscs_pdrh   
77       tfmri_mr1_alvn_bscs_hpusrh   
78         tfmri_mr1_alvn_bscs_ayrh   
79         tfmri_mr1_alvn_bscs_aarh   
80       tfmri_mr1_alvn_bscs_vtdcrh   
81     tfmri_mr1_rpvnfb_bscs_cbwmlh   
82      tfmri_mr1_rpvnfb_bscs_lvelh   
83     tfmri_mr1_rpvnfb_bscs_iftvlh   
84    tfmri_mr1_rpvnfb_bscs_crbwmlh   
85    tfmri_mr1_rpvnfb_bscs_crbcxlh   
86       tfmri_mr1_rpvnfb_bscs_tplh   
87      tfmri_mr1_rpvnfb_bscs_ctelh   
88       tfmri_mr1_rpvnfb_bscs_pulh   
89       tfmri_mr1_rpvnfb_bscs_pdlh   
90   tfmri_mr1_rpvnfb_bscs_3rdvicle   
91   tfmri_mr1_rpvnfb_bscs_4thvicle   
92         tfmri_mr1_rpvnfb_bscs_bs   
93     tfmri_mr1_rpvnfb_bscs_hpuslh   
94       tfmri_mr1_rpvnfb_bscs_aylh   
95        tfmri_mr1_rpvnfb_bscs_csf   
96       tfmri_mr1_rpvnfb_bscs_aalh   
97     tfmri_mr1_rpvnfb_bscs_vtdclh   
98     tfmri_mr1_rpvnfb_bscs_cbwmrh   
99      tfmri_mr1_rpvnfb_bscs_lverh   
100     tfmri_mr1_rpvnfb_bscs_iftvh   
101   tfmri_mr1_rpvnfb_bscs_crbwmrh   
102   tfmri_mr

In [30]:
table.head()

collection_id  abcd_midr1bwp101_id  dataset_id        subjectkey  \
0           2573                25977       17008  NDAR_INVPRX26ZJ6   
1           2573                25894       17008  NDAR_INVP74XG4NJ   
2           2573                25897       17008  NDAR_INVPAFJ1FYV   
3           2573                26219       17008  NDAR_INVTDK7YAGN   
4           2573                26729       17008  NDAR_INVX5TLCB96   

     src_subject_id interview_date  interview_age gender  \
0  NDAR_INVPRX26ZJ6     08/03/2017            126      M   
1  NDAR_INVP74XG4NJ     08/13/2017            127      F   
2  NDAR_INVPAFJ1FYV     02/28/2017            118      M   
3  NDAR_INVTDK7YAGN     01/11/2017            114      M   
4  NDAR_INVX5TLCB96     02/03/2017            120      F   

               eventname tfmri_mid_run1_beta_visitid  tfmri_mid_run1_beta_tr  \
0  baseline_year_1_arm_1   S086_INVPRX26ZJ6_20170804                     0.8   
1  baseline_year_1_arm_1   S053_INVP74XG4NJ_20170815                     0.8   
2  baseline_year_1_arm_1                         NaN                     NaN   
3  baseline_year_1_arm_1   S014_INVTDK7YAGN_20170112                     0.8   
4  baseline_year_1_arm_1   G075_INVX5TLCB96_20170204                     0.8   

   tfmri_mid_run1_beta_numtrs  tfmri_mid_run1_beta_dof  \
0                       411.0                    357.0   
1                       411.0                    356.0   
2                         NaN                      NaN   
3                       411.0                    355.0   
4                       408.0                    357.0   

   tfmri_mid_run1_beta_nvols  tfmri_mr1_beta_stnvols  tfmri_mr1_beta_mm  \
0                      403.0                   403.0           0.112381   
1                      403.0                   402.0           0.110862   
2                        NaN                     NaN                NaN   
3                      403.0                   401.0           0.129190   
4                      403.0                   403.0           0.103592   

   tfmri_mr1_beta_maxmotion  tfmri_mr1_beta_meantrans  \
0                  0.376639                  0.079786   
1                  2.247453                  0.074324   
2                       NaN                       NaN   
3                  1.327166                  0.063572   
4                  0.606095                  0.065073   

   tfmri_mid_run1_beta_maxtrans  tfmri_mid_run1_beta_meanrot  \
0                      0.213983                     0.032595   
1                      0.579568                     0.036539   
2                           NaN                          NaN   
3                      0.433347                     0.065619   
4                      0.349409                     0.038519   

   tfmri_mid_run1_beta_maxrot  tfmri_mr1_arvn_bscs_cbwmlh  \
0                    0.255165                    0.037281   
1                    1.667886                    0.022032   
2                         NaN                         NaN   
3                    0.893818                   -0.047518   
4                    0.294982                    0.036175   

   tfmri_mr1_arvn_bscs_lvelh  tfmri_mr1_arvn_bscs_iftvlh  \
0                   0.091545                   -0.079452   
1                   0.108968                    0.150200   
2                        NaN                         NaN   
3                   0.159354                    0.233076   
4                   0.066631                   -0.111081   

   tfmri_mr1_arvn_bscs_crbwmlh  tfmri_mr1_arvn_bscs_crbcxlh  \
0                     0.262569                     0.574847   
1                     0.131209                     0.310600   
2                          NaN                          NaN   
3                    -0.139507                    -0.160790   
4                    -0.037344                    -0.129689   

   tfmri_mr1_arvn_bscs_tplh  tfmri_mr1_arvn_bscs_ctelh  \
0                  0.163567              

In [31]:
new_table.head()

collection_id  abcd_midr1bwp201_id  dataset_id        subjectkey  \
0           2573                21365       17008  NDAR_INVP9Y862GP   
1           2573                20951       17008  NDAR_INVL1UHN7LG   
2           2573                21723       17008  NDAR_INVTH3T33V5   
3           2573                21599       17008  NDAR_INVRMTJ44GE   
4           2573                21670       17008  NDAR_INVT9F6AYDG   

     src_subject_id interview_date  interview_age gender  \
0  NDAR_INVP9Y862GP     08/02/2017            127      M   
1  NDAR_INVL1UHN7LG     07/07/2017            111      F   
2  NDAR_INVTH3T33V5     02/05/2017            117      F   
3  NDAR_INVRMTJ44GE     02/06/2017            123      F   
4  NDAR_INVT9F6AYDG     03/08/2017            124      M   

   tfmri_mr1_alvsl_bscs_vtdcrh  tfmri_mr1_arvn_bcdk_bstslh  \
0                     0.196214                    0.045481   
1                     0.270360                   -0.022267   
2                     0.265873                   -0.052331   
3                     0.412290                   -0.168477   
4                     0.157333                   -0.092918   

   tfmri_mr1_arvn_bcdk_cdatcglh  tfmri_mr1_arvn_bcdk_cdmdftlh  \
0                     -0.201054                     -0.147813   
1                      0.193977                     -0.321201   
2                     -0.112673                     -0.077043   
3                     -0.048458                      0.001702   
4                     -0.139001                     -0.050428   

   tfmri_mr1_arvn_bcdk_culh  tfmri_mr1_arvn_bcdk_ehinallh  \
0                 -0.378059                     -0.146332   
1                 -0.024790                      1.545470   
2                  0.179620                      0.395220   
3                 -0.488868                     -1.111801   
4                 -0.099799                      0.874351   

   tfmri_mr1_arvn_bcdk_fflh  tfmri_mr1_arvn_bcdk_ifpalh  \
0                 -0.087141                   -0.142583   
1                 -0.061648                   -0.210334   
2                  0.018941                    0.041472   
3                  0.202283                   -0.184950   
4                  0.039836                   -0.033324   

   tfmri_mr1_arvn_bcdk_iftplh  tfmri_mr1_arvn_bcdk_ihcglh  \
0                    0.263493                   -0.092636   
1                   -0.266555                   -0.284074   
2                   -0.153870                    0.234149   
3                   -0.282212                   -0.199092   
4                    0.335035                    0.044682   

   tfmri_mr1_arvn_bcdk_laocclh  tfmri_mr1_arvn_bcdk_laobftlh  \
0                     0.051846                     -0.600417   
1                    -0.260318                      0.131703   
2                    -0.059226                     -0.105404   
3                    -0.819251                     -0.873140   
4                     0.154712                     -0.076867   

   tfmri_mr1_arvn_bcdk_lglh  tfmri_mr1_arvn_bcdk_mobftlh  \
0                 -0.258148                    -1.177860   
1                 -0.092822                     0.207424   
2                  0.103602                    -0.249645   
3                  0.115916                    -1.479815   
4                 -0.074575                     0.090530   

   tfmri_mr1_arvn_bcdk_mdtplh  tfmri_mr1_arvn_bcdk_pahpallh  \
0                    0.009439                     -0.260763   
1                   -0.125765                     -0.106484   
2                   -0.116509                      0.105293   
3                   -0.014715                     -0.126644   
4                    0.003518                     -0.024255   

   tfmri_mr1_arvn_bcdk_pacnlh  tfmri_mr1_arvn_bcdk_psoprcslh  \
0                   -0.031511                      -0.207526   
1                   -0.147179                       0.160174   
2                    0.104741                

In [90]:
# Load Monetary Incentive Delay data
mid_paths = ['gordonp101','gordonp201','gordonp301', 'gordonp401']
mid_paths = [abcd_table_path + pp + '.txt' for pp in mid_paths]

mid_contrasts = ['MID anticipation of reward versus neutral',
       'MID anticipation of loss versus neutral',
       'MID reward positive versus negative feeback',
       'MID loss positive versus negative feedback',
       'MID anticipation of large reward versus neutral',
       'MID anticipation of small reward versus neutral',
       'MID anticipation of large versus small reward',
       'MID anticipation of large loss versus neutral',
       'MID anticipation of small loss versus neutral',
       'MID anticipation of small versus large loss']

mid_b_melt, mid_l = load_task_melt_contrasts(mid_paths, mid_contrasts, 'mid')

# Load Stop Signal Task

sst_paths = ['mrisstp101','mrisstp201', 'mrisstp301']
sst_paths = [abcd_table_path + pp + '.txt' for pp in sst_paths]

sst_contrasts = ['SST correct go versus fixation',
       'SST correct stop versus correct go',
       'SST incorrect stop versus correct go',
       'SST any stop versus correct go',
       'SST correct stop versus incorrect stop',
       'SST incorrect go versus correct go',
       'SST incorrect go versus incorrect stop']

sst_b_melt, sst_l = load_task_melt_contrasts(sst_paths, sst_contrasts, 'sst')


nb_paths = ['nbackgordonp101','nbackgordonp201', 'nbackgordonp301', 'nbackgordonp401']
nb_paths = [abcd_table_path + pp+'.txt' for pp in nb_paths]

nb_contrasts = ['nBack 0 back condition', 'nBack 2 back condition',
       'nBack place condition',
       'nBack emotion condition',
       'nBack 2 back versus 0 back contrast',
       'nBack face versus place contrast',
       'nBack emotion versus neutral face contrast',
       'nBack negative face versus positive face contrast',
       'nBack positive face versus neutral face contrast']

nb_b_melt, nb_l = load_task_melt_contrasts(nb_paths, nb_contrasts, 'nb')

/data/nielsond/python/envs/py3_c/lib/python3.6/site-packages/ipykernel_launcher.py:75: FutureWarning: Sorting because non-concatenation axis is not aligned. A future version
of pandas will change to not sort by default.

To accept the future behavior, pass 'sort=False'.

To retain the current behavior and silence the warning, pass 'sort=True'.



In [91]:
tb_b = pd.concat([mid_b_melt, sst_b_melt, nb_b_melt])
tb_b = tb_b.merge(for_balancing.loc[:,['subjectkey','eventname','ehi_y_ss_scoreb','scanner_manufacturer_pd',
            'scanner_type_pd', 'deviceserialnumber']],
                  how='left',
                  on=['subjectkey','eventname'])

/data/nielsond/python/envs/py3_c/lib/python3.6/site-packages/ipykernel_launcher.py:1: FutureWarning: Sorting because non-concatenation axis is not aligned. A future version
of pandas will change to not sort by default.

To accept the future behavior, pass 'sort=False'.

To retain the current behavior and silence the warning, pass 'sort=True'.

  """Entry point for launching an IPython kernel.
/data/nielsond/python/envs/py3_c/lib/python3.6/site-packages/pandas/core/indexing.py:1472: FutureWarning: 
Passing list-likes to .loc or [] with any missing label will raise
KeyError in the future, you can use .reindex() as an alternative.

See the documentation here:
https://pandas.pydata.org/pandas-docs/stable/indexing.html#deprecate-loc-reindex-listlike
  return self._getitem_tuple(key)


In [92]:
tb_b.head()

collection_id                                     collection_title  \
0           2573  Adolescent Brain Cognitive Development Study (ABCD)   
1           2573  Adolescent Brain Cognitive Development Study (ABCD)   
2           2573  Adolescent Brain Cognitive Development Study (ABCD)   
3           2573  Adolescent Brain Cognitive Development Study (ABCD)   
4           2573  Adolescent Brain Cognitive Development Study (ABCD)   

                                    contrast  dataset_id  \
0  MID anticipation of reward versus neutral       14688   
1  MID anticipation of reward versus neutral       14688   
2  MID anticipation of reward versus neutral       14688   
3  MID anticipation of reward versus neutral       14688   
4  MID anticipation of reward versus neutral       14688   

               eventname  fmri_beta_gparc_mean_motion  fmri_beta_gparc_numtrs  \
0  baseline_year_1_arm_1                     0.248041                     822   
1  baseline_year_1_arm_1                     0.182486                     822   
2  baseline_year_1_arm_1                     0.455445                     822   
3  baseline_year_1_arm_1                     0.262064                     822   
4  baseline_year_1_arm_1                     0.133744                     822   

   fmri_beta_gparc_tr gender  interview_age interview_date     lhgp1  \
0                 0.8      M            130     08/22/2017 -0.425044   
1                 0.8      F            118     03/21/2017 -0.060055   
2                 0.8      F            132     03/20/2017  0.030440   
3                 0.8      F            128     03/11/2017 -0.172401   
4                 0.8      M            128     08/16/2017  0.148744   

     lhgp10   lhgp100   lhgp101   lhgp102   lhgp103   lhgp104   lhgp105  \
0 -0.278981 -0.330238 -0.659327 -0.100991 -0.164087 -0.069778 -0.259956   
1  0.223353  0.039213  0.156407  0.127468  0.192140  0.210434  0.052907   
2 -0.050951  0.444189 -0.448928 -0.263181 -0.335745 -0.154088 -0.116380   
3 -0.147176 -0.231836 -1.353622 -0.163668 -0.267727 -0.393743 -0.255218   
4  0.112254  0.057920  0.090639  0.059643  0.178707  0.039961  0.064841   

    lhgp106   lhgp107   lhgp108   lhgp109    lhgp11   lhgp110   lhgp111  \
0  0.027596 -0.123254  0.060143 -0.011697 -0.202914  0.038294 -0.231322   
1  0.190758  0.154290  0.060324  0.276541  0.441786  0.317228 -0.054601   
2 -0.159730 -0.293752 -0.033334  0.027833 -1.019016 -0.436428 -0.112745   
3 -0.112664 -0.304311 -0.181995 -0.516308  0.836315 -0.619614 -0.477287   
4  0.120451  0.107930 -0.075844 -0.007143  0.057674  0.085236  0.077351   

    lhgp112   lhgp113   lhgp114   lhgp115   lhgp116   lhgp117   lhgp118  \
0  0.202921 -0.042618  0.053599  0.326953  0.399547 -0.188769 -0.038583   
1  0.139377  0.019372 -1.542622  1.913331 -0.409703 -0.110641 -0.140633   
2 -0.233389  0.081919 -0.178405  0.048678  0.219419 -0.068672 -0.585321   
3 -0.349361 -0.868203 -0.669437 -1.061908 -0.434773  0.184057 -0.248093   
4  0.047557 -0.108195 -0.241988 -0.062457 -0.127053 -0.243706  0.392318   

    lhgp119    lhgp12   lhgp120   lhgp121   lhgp122   lhgp123   lhgp124  \
0 -0.436554 -0.069368  0.182393  0.436207  0.141061  0.457829 -0.964506   
1 -1.069615  0.089542 -0.310029 -1.671225 -0.735321  0.249405 -0.150334   
2  0.015703  0.193118 -0.239572 -0.197256 -0.107839 -1.790290  0.923048   
3 -0.397071 -0.134931 -0.051787 -1.868795  0.638810  0.817106  0.825435   
4 -0.034673  0.165411 -0.096396  0.079171 -0.421901 -0.805389 -1.446214   

    lhgp125   lhgp126   lhgp127   lhgp128   lhgp129    lhgp13   lhgp130  \
0  1.184777  0.084250 -0.180462 -0.002004 -0.278521 -0.252325 -0.377267   
1 -0.357947 -0.057521 -0.070272  0.387101  0.496546  0.187253  0.023798   
2 -5.310752  0.286600  0.163611  0.570576 -0.846637 -0.257804  0.019195   
3 -0.094657  0.651311 -0.222972  0.801287  0.201437 -0.136286 -0.263199   
4 -2.697301 -0.111079 -0.123756  0.026545  0.103457  0.098371 -0.066665   

    lhgp131   lhgp132   lhgp

# Filter out bad scans


In [76]:
qc_t, qc_l = load_abcd_table(abcd_table_path + 'mriqc01.txt')
qc_t = qc_t.rename(columns={'visit':'eventname'})

In [77]:
qc_cols = ['iqc_rsfmri_good_ser',
 'iqc_mid_good_ser',
 'iqc_sst_good_ser',
 'iqc_nback_good_ser']

In [78]:
scan_types = ['rsfmri','nback','mid','sst']
qc_col_pat = 'iqc_%s_good_ser'
for st in scan_types:
    col = qc_col_pat%st
    if st == 'rsfmri':
         qc_t[st+'_ok'] = (qc_t.loc[:,col]==4).astype(bool)
    else:
        qc_t[st+'_ok'] = (qc_t.loc[:,col]==2).astype(bool)
#qc_ok_cols = ['iqc_%s_1_qc_score'%st for st in scan_types]

In [79]:
(qc_t.loc[:, qc_cols]==2).sum()

iqc_rsfmri_good_ser     378
iqc_mid_good_ser       3299
iqc_sst_good_ser       3215
iqc_nback_good_ser     3151
dtype: int64

In [80]:
con = con.merge(qc_t.loc[:, ['subjectkey', 'eventname', 'rsfmri_ok']], how='left', on=['subjectkey','eventname']).head()

In [81]:
con = con.rename(columns={'rsfmri_ok':'qc_ok'})

In [82]:
con.query('qc_ok == 0')

collection_id  dataset_id        subjectkey    src_subject_id  \
0           2573       14688  NDAR_INV00X2TBWJ  NDAR_INV00X2TBWJ   
2           2573       14688  NDAR_INV02H7G2T6  NDAR_INV02H7G2T6   

  interview_date  interview_age gender              eventname  \
0     05/12/2017            130      F  baseline_year_1_arm_1   
2     11/19/2016            119      F  baseline_year_1_arm_1   

                       visit  rsfm_tr  rsfm_nreps  rsfm_numtrs  \
0  S020_INV00X2TBWJ_20170512      0.8        1149         1149   
2  P043_INV02H7G2T6_20161119      0.8        1532         1532   

   rsfm_mean_motion  rsfm_max_motion  rsfm_mean_trans  rsfm_max_trans  \
0          0.496881        10.471224         0.321085        7.829029   
2          0.229100         2.415015         0.159073        1.318155   

   rsfm_mean_rot  rsfm_max_rot  scanner_manufacturer_pd  scanner_type_pd  \
0       0.201447      3.939768                  SIEMENS           Prisma   
2       0.080244      1.263554  Philips Medical Systems  Achieva dStream   

  deviceserialnumber  magnetic_field_strength pipeline_version    procdate  \
0       HASH11ad4ed5                        3              DJH  10/20/2017   
2       HASHdb2589d4                        3              DJH  01/14/2018   

   rsfm_auditory_to_auditory  rsfm_auditory_to_cingulooperc  \
0                   0.066845                       0.073088   
2                   0.240388                       0.199407   

   rsfm_auditory_to_cingulopar  rsfm_auditory_to_default  \
0                    -0.001011                  0.033577   
2                    -0.109374                  0.009745   

   rsfm_auditory_to_dorsalattn  rsfm_auditory_to_frontopariet  \
0                    -0.040924                       0.012529   
2                    -0.013361                       0.026148   

   rsfm_auditory_to_none  rsfm_aud_to_retsplenialtem  rsfm_auditory_to_smhand  \
0              -0.000868                   -0.022256                 0.033541   
2               0.000021                   -0.103312                 0.041118   

   rsfm_auditory_to_smmouth  rsfm_auditory_to_salience  \
0                  0.050652                   0.061032   
2                  0.069293                   0.223491   

   rsfm_auditory_to_ventralattn  rsfm_auditory_to_visual  \
0                      0.076112                -0.043698   
2                      0.165321                -0.138923   

   rsfm_cingulooperc_to_auditory  rsfm_copc_to_copc  \
0                       0.046152           0.288730   
2                       0.211595           0.193768   

   rsfm_copc_to_cinguloparietal  rsfm_copc_to_default  \
0                     -0.176042             -0.093068   
2                     -0.081509              0.022021   

   rsfm_copc_to_dorsalattn  rsfm_copc_to_frontoparietal  \
0                 0.147775                    -0.033703   
2                -0.007543                     0.026849   

   rsfm_cingulooperc_to_none  rsfm_copc_to_retsplenialtem  \
0                  -0.066793                    -0.053857   
2                  -0.015032                    -0.076462   

   rsfm_cingulooperc_to_smhand  rsfm_cingulooperc_to_smmouth  \
0                     0.118360                     -0.017932   
2                     0.075341                      0.107894   

   rsfm_cingulooperc_to_salience  rsfm_copc_to_ventralattn  \
0                       0.172659                  0.019018   
2                       0.210513                  0.128994   

   rsfm_cingulooperc_to_visual  rsfm_cpar_to_auditory  \
0                    -0.098322               -0.00115   
2                    -0.137512               -0.05493   

   rsfm_cpar_to_cingulooperc  rsfm_cpar_to_cpar  rsfm_cpar_to_default  \
0                  -0.032795          -0.000344              0.075480   
2                  -0.053695           0.115973              0.017563   

   rsfm_cpar_to_dorsalattn  rsfm_cpar_to_frontoparietal  \
0                -0.0

In [83]:
tb_qc = []
for st in scan_types:
    if st != 'rsfmri':
        tmpdf = qc_t.loc[:, ['subjectkey', 'eventname', st+'_ok']].rename(columns={st+'_ok':'qc_ok'})
        if st == 'nback':
            tmpdf['task'] = 'nb'
        else:
            tmpdf['task'] = st
        tb_qc.append(tmpdf)
tb_qc = pd.concat(tb_qc)

In [84]:
tb_qc.task.unique()
tb_t.task.unique()


array(['nb', 'mid', 'sst'], dtype=object)

array(['mid', 'sst', 'nb'], dtype=object)

In [85]:
tb_t.merge(tb_qc, how='outer', on=['subjectkey', 'eventname', 'task'], indicator=True).groupby('_merge').count()
tb_b.merge(tb_qc, how='outer', on=['subjectkey', 'eventname', 'task'], indicator=True).groupby('_merge').count()

collection_id  collection_title  contrast  dataset_id  eventname  \
_merge                                                                         
left_only               0                 0         0           0          0   
right_only              0                 0         0           0       4111   
both               245461            245461    245461      245461     245461   

            fmri_beta_gparc_mean_motion  fmri_beta_gparc_numtrs  \
_merge                                                            
left_only                             0                       0   
right_only                            0                       0   
both                             245461                  245461   

            fmri_beta_gparc_tr  gender  interview_age  interview_date   lhgp1  \
_merge                                                                          
left_only                    0       0              0               0       0   
right_only                   0       0              0               0       0   
both                    245461  245461         245461          245461  161863   

            lhgp10  lhgp100  lhgp101  lhgp102  lhgp103  lhgp104  lhgp105  \
_merge                                                                     
left_only        0        0        0        0        0        0        0   
right_only       0        0        0        0        0        0        0   
both        161819   161877   161819   161819   161812   161819   161863   

            lhgp106  lhgp107  lhgp108  lhgp109  lhgp11  lhgp110  lhgp111  \
_merge                                                                     
left_only         0        0        0        0       0        0        0   
right_only        0        0        0        0       0        0        0   
both         161870   161863   161863   161863  161723   161863   161819   

            lhgp112  lhgp113  lhgp114  lhgp115  lhgp116  lhgp117  lhgp118  \
_merge                                                                      
left_only         0        0        0        0        0        0        0   
right_only        0        0        0        0        0        0        0   
both         161819   161819   161802   161802   161826   161826   161767   

            lhgp119  lhgp12  lhgp120  lhgp121  lhgp122  lhgp123  lhgp124  \
_merge                                                                     
left_only         0       0        0        0        0        0        0   
right_only        0       0        0        0        0        0        0   
both         161754  161819   161768   161733   161740   161754   161669   

            lhgp125  lhgp126  lhgp127  lhgp128  lhgp129  lhgp13  lhgp130  \
_merge                                                                     
left_only         0        0        0        0        0       0        0   
right_only        0        0        0        0        0       0        0   
both         161464   161804   161849   161740   161744  161812   161863   

            lhgp131  lhgp132  lhgp133  lhgp134  lhgp135  lhgp136  lhgp137  \
_merge                                                                      
left_only         0        0        0        0        0        0        0   
right_only        0        0        0        0        0        0        0   
both         161835   161835   161747   161367   161747   161819   161856   

            lhgp138  lhgp139  lhgp14  lhgp140  lhgp141  lhgp142  lhgp143  \
_merge                                                                     
left_only         0        0       0        0        0        0        0   
right_only        0        0       0        0        0        0        0   
both         161856   161842  161819   161818   161849   161754   161835   

            lhgp144  lhgp145  lhgp146  lhgp147  lhgp148  lhgp149  lhgp15  \
_merge                                                                     
left_only         0        0        0   

collection_id  collection_title  contrast  dataset_id  eventname  \
_merge                                                                         
left_only               0                 0         0           0          0   
right_only              0                 0         0           0       4111   
both               245461            245461    245461      245461     245461   

            fmri_beta_gparc_mean_motion  fmri_beta_gparc_numtrs  \
_merge                                                            
left_only                             0                       0   
right_only                            0                       0   
both                             245461                  245461   

            fmri_beta_gparc_tr  gender  interview_age  interview_date   lhgp1  \
_merge                                                                          
left_only                    0       0              0               0       0   
right_only                   0       0              0               0       0   
both                    245461  245461         245461          245461  245275   

            lhgp10  lhgp100  lhgp101  lhgp102  lhgp103  lhgp104  lhgp105  \
_merge                                                                     
left_only        0        0        0        0        0        0        0   
right_only       0        0        0        0        0        0        0   
both        245204   245289   245204   245204   245197   245204   245275   

            lhgp106  lhgp107  lhgp108  lhgp109  lhgp11  lhgp110  lhgp111  \
_merge                                                                     
left_only         0        0        0        0       0        0        0   
right_only        0        0        0        0       0        0        0   
both         245282   245275   245275   245275  245108   245275   245204   

            lhgp112  lhgp113  lhgp114  lhgp115  lhgp116  lhgp117  lhgp118  \
_merge                                                                      
left_only         0        0        0        0        0        0        0   
right_only        0        0        0        0        0        0        0   
both         245204   245204   245187   245187   245229   245229   245170   

            lhgp119  lhgp12  lhgp120  lhgp121  lhgp122  lhgp123  lhgp124  \
_merge                                                                     
left_only         0       0        0        0        0        0        0   
right_only        0       0        0        0        0        0        0   
both         245157  245204   245171   245136   245134   245157   245027   

            lhgp125  lhgp126  lhgp127  lhgp128  lhgp129  lhgp13  lhgp130  \
_merge                                                                     
left_only         0        0        0        0        0       0        0   
right_only        0        0        0        0        0       0        0   
both         244732   245198   245261   245098   245147  245197   245275   

            lhgp131  lhgp132  lhgp133  lhgp134  lhgp135  lhgp136  lhgp137  \
_merge                                                                      
left_only         0        0        0        0        0        0        0   
right_only        0        0        0        0        0        0        0   
both         245247   245229   245123   244518   245159   245195   245259   

            lhgp138  lhgp139  lhgp14  lhgp140  lhgp141  lhgp142  lhgp143  \
_merge                                                                     
left_only         0        0       0        0        0        0        0   
right_only        0        0       0        0        0        0        0   
both         245259   245236  245204   245131   245216   245139   245247   

            lhgp144  lhgp145  lhgp146  lhgp147  lhgp148  lhgp149  lhgp15  \
_merge                                                                     
left_only         0        0        0   

In [86]:
tb_t = tb_t.merge(tb_qc, how='left', on=['subjectkey', 'eventname', 'task'])
tb_b = tb_b.merge(tb_qc, how='left', on=['subjectkey', 'eventname', 'task'])

In [87]:
con.to_pickle(data_dir/'con.pkz')
tb_t.to_pickle(data_dir/'task_based_tstats.pkz')
tb_b.to_pickle(data_dir/'task_based_betas.pkz')